In [127]:
import numpy as np
import pandas as pd
import string
import os
from collections import Counter
import copy

import nltk
from nltk.tokenize import sent_tokenize, word_tokenize

from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
pd.options.display.max_colwidth = 50
pd.set_option('display.max_rows', 500)
import re

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD

# Creating base

In [128]:
new_test=pd.read_csv('..//bases/new_test_variants.csv')
new_test_texts = pd.read_csv('..//bases/new_test_text.csv', sep="\|\|", engine='python', header=None, skiprows=1, names=["ID","Text"], encoding = "utf-8")
new_test_final=pd.merge(new_test,new_test_texts,how="left",on="ID")

In [129]:
leaks=pd.read_csv('..//bases/s1_add_train.csv')
leaks_1=pd.DataFrame([leaks["ID"],leaks.drop("ID",axis=1).idxmax(axis=1).map(lambda x: x.lstrip('class'))])
leaks_2=leaks_1.T
leaks_2.columns=["ID","Class"]

In [130]:
train = pd.read_csv('..//bases/training_variants')
test = pd.read_csv('..//bases/test_variants')

In [131]:
train_texts = pd.read_csv('..//bases/training_text', sep="\|\|", engine='python', header=None, skiprows=1, names=["ID","Text"], encoding = "utf-8")
test_texts = pd.read_csv('..//bases/test_text', sep="\|\|", engine='python', header=None, skiprows=1, names=["ID","Text"], encoding = "utf-8")

In [132]:
train = pd.merge(train, train_texts, how='left', on='ID')
test = pd.merge(test, test_texts, how='left', on='ID')

In [133]:
leaks_3=pd.merge(leaks_2,test[test.ID.isin(leaks_2.ID)])
leaks_final=pd.merge(leaks_3,test_texts[test_texts.ID.isin(leaks_3.ID)])

In [134]:
train_all = pd.concat([train,leaks_final]) #adding first stage

In [135]:
merge_match = new_test.merge(train_all, left_on=['Gene', 'Variation'], right_on = ['Gene', 'Variation'])
Index_leak = merge_match.ID_x - 1
new_test_index = [item for item in new_test_final.index if item not in list(Index_leak)]
test_no_leaks = new_test_final.iloc[new_test_index]
test_no_leaks

ID       Gene Variation  \
2      3       WNT4     E216G   
3      4     SUCLA2     G118R   
5      6      CHEK2     E239K   
6      7      CHST3     T141M   
7      8       RNF6     G244D   
8      9      SPAST     C448Y   
10    11      SCN4A     V445M   
14    15      ERBB2     G746S   
15    16       TP53     Y234S   
16    17     RAB27A      A87P   
17    18       EGFR     P546S   
18    19      ERBB2     G279E   
19    20      CSF1R     Y969H   
21    22     SLC7A9     V170M   
22    23   ADAMTS13     A250V   
24    25    DYNC2H1    Q1537R   
26    27      TRPM1      L99P   
27    28      SCN9A     N641Y   
29    30     CYP7B1     F216S   
30    31       SYT6     A406T   
31    32      BCS1L     S277N   
33    34      SCN9A     P149Q   
34    35      SCN9A    I1461T   
35    36       SCO1     P174L   
37    38      CSF1R     Y969F   
38    39       GJB3     E183K   
41    42       TSHR     P162A   
42    43      SMAD4     G386C   
45    46    SLC17A5     P334R   
46    47      ERBB2     V762M   
47    48       GJB3      C86S   
49    50        MET    M1268T   
50    51      RPS26      D33N   
52    53      RPS26       M1L   
53    54       KRAS      Q61K   
54    55       TSHR     R109Q   
55    56   SLC25A15     R275Q   
57    58      STK11     G163C   
58    59      ABCC6    R1138Q   
60    61      WISP3     S334P   
62    63     PHOX2B     R100L   
65    66       TSHR     C390W   
66    67     PTPN11      A72D   
68    69    B4GALT7     R270C   
69    70    ALOX12B     H578Q   
70    71       LRP4     D449N   
72    73     PIK3CA     E545D   
75    76       LRP4     D529N   
77    78      SMAD4     D355E   
79    80        GNE     R266W   
80    81      SPAST      S44L   
82    83        GNE     V572L   
84    85      RBBP8     K337E   
85    86     KISS1R     L148S   
86    87        DCC    P1375H   
89    90       CILP     I395T   
90    91      KCNQ4     W276S   
92    93    DYNC2H1    M1991L   
93    94    SLC19A2      P51L   
95    96       LRP6     R611C   
96    97     SLC7A9     G259R   
97    98       TSHR     M453T   
99   100    SLC17A5     H183R   
100  101      ABCC6    R1114P   
102  103       TP53     R273S   
103  104      ACVR1     R258M   
104  105   SLC25A15      G27R   
105  106     PIK3CA    G1049S   
106  107   SLC25A15      L71Q   
107  108       LRP5     R752G   
108  109  TNFRSF11A      G53R   
110  111      ABCC6    R1459C   
112  113       ASS1     R108L   
115  116       TSHR     P639S   
116  117       TSHR     F631L   
118  119     RAB27A     A152P   
119  120      PRKRA     P222L   
123  124       OTOF    P1825A   
124  125       BBS5     T183A   
125  126       CRB1     V162M   
127  128      ABCC6    R1138W   
128  129       IDH2     R140W   
129  130     IKBKAP     R696P   
131  132      SMAD4     G386S   
132  133      SCN9A     L858H   
133  134     CREBBP    R1446G   
134  135     NDUFS3     R199W   
135  136       MYOT      S60C   
136  137     NDUFS6     C115Y   
137  138      CSF1R     Y571D   
139  140      SCN9A    V1299F   
141  142      DNAI1     G515S   
142  143        GNE     G607E   
143  144      STK11      R86G   
144  145     PLA2G6      A80T   
147  148      SCN4A    V1293I   
148  149       EDAR     R375H   
149  150      SEPT9      R88W   
150  151       WNT4     A114V   
152  153       POLH     K589T   
154  155     SLC7A7      G54V   
155  156       AKT2     S302G   
156  157       OTOF    L1011P   
157  158      SCN4A    I1160V   
159  160      SCN9A      I62V   
160  161        MYC      P58L   
161  162       LRP5     A214V   
162  163      SCN4A    R1448C   
164  165       TP53     S241A   
165  166       TP63     R352G   
167  168      SCN4A    L1433R   
169  170       SCO2     E140K   
170  171      WISP3     C145Y   
171  172      EPAS1     G537W   
176  177     NDUFS3     T145I   
179  180       TP63     C561G   
180  181       FLNB     S235P   
182  183      SCN4A    V1589M   
183  184       TP63     L553F   
184  185      SCN4A    M1592V   
186  187     

In [136]:
train_all['Substitutions_var'] = train_all.Variation.apply(lambda x: bool(re.search('^[A-Z]\\d+[A-Z*]$', x))*1)
new_train = train_all[train_all['Substitutions_var']==1]

In [137]:
#### process the train and test set together
data_all = pd.concat((new_train, test_no_leaks), axis=0, ignore_index=True)
data_all = data_all[['Class', 'Gene', 'ID', 'Variation', 'Text']] # just reordering
data_all_backup = data_all[:] ## We keep backup in case we need to use again
data_all

Class       Gene   ID Variation  \
0        2        CBL    1     W802*   
1        2        CBL    2     Q249E   
2        3        CBL    3     N454D   
3        4        CBL    4     L399V   
4        4        CBL    5     V391I   
5        5        CBL    6     V430M   
6        4        CBL    8     Y371H   
7        4        CBL    9     C384R   
8        4        CBL   10     P395A   
9        4        CBL   11     K382E   
10       4        CBL   12     R420Q   
11       4        CBL   13     C381A   
12       5        CBL   14     P428L   
13       4        CBL   15     D390Y   
14       4        CBL   17     Q367P   
15       5        CBL   18     M374V   
16       4        CBL   19     Y371S   
17       6        CBL   20      H94Y   
18       4        CBL   21     C396R   
19       4        CBL   22     G375P   
20       4        CBL   23     S376F   
21       4        CBL   24     P417A   
22       4        CBL   25     H398Y   
23       4      SHOC2   26       S2G   
24       4       TERT   27     Y846C   
25       7       TERT   28     C228T   
26       4       TERT   29     H412Y   
27       4       TERT   30     H876Q   
28       4       TERT   32     P704S   
29       7       TERT   34     C250T   
30       4     DICER1   35    G1809R   
31       4     DICER1   36    G1809K   
32       1     DICER1   37    D1709E   
33       1     DICER1   38    D1709A   
34       4     DICER1   39    E1705A   
35       4     DICER1   40    D1810A   
36       4     DICER1   42    E1705K   
37       4      PTPRT   44    T1365M   
38       1      PTPRT   45     V648G   
39       4      PTPRT   46     T844M   
40       1      PTPRT   47     A707T   
41       4      PTPRT   49    R1343L   
42       1      PTPRT   50     A209T   
43       1      PTPRT   51     Y280H   
44       4      PTPRT   52     D927G   
45       1      PTPRT   53     N510K   
46       1      PTPRT   54     F248S   
47       1      PTPRT   55     L708P   
48       4      PTPRT   56     V995M   
49       1      PTPRT   57     Y412F   
50       1      PTPRT   58      F74S   
51       1      PTPRT   59    R1040L   
52       1      PTPRT   60     R453C   
53       4      PTPRT   61    R1209W   
54       4      PTPRT   62    A1022E   
55       4      PTPRT   63     Q984K   
56       1      PTPRT   64     T605M   
57       1      PTPRT   65     K218T   
58       4      PTPRT   66    N1125I   
59       7       RHEB   67      Y35C   
60       7       RHEB   68      Y35N   
61       7       RHEB   69      Y35H   
62       4      RAD50   73    L1273F   
63       2      CCND3   76     P284L   
64       7      CCND3   77     Q276*   
65       7      CCND3   78     T286A   
66       7      CCND3   79     T283A   
67       2      CCND3   80     I290A   
68       2      CCND3   81     I290R   
69       7       RIT1   82      A77S   
70       7       RIT1   83      A77P   
71       2       RIT1   84      A77T   
72       7       RIT1   85      M90I   
73       4     TGFBR1   89      N45S   
74       1     TGFBR1   90     R487Q   
75       4     TGFBR1   91      C41Y   
76       4     TGFBR1   92      G52R   
77       4     TGFBR1   93      P83L   
78       1     TGFBR1   94     S241L   
79       4     TGFBR1   95     S387Y   
80       2     TGFBR2   97     R537P   
81       4     TGFBR2   98     D404G   
82       4     TGFBR2   99     P525L   
83       4       MSH6  102     R922*   
84       1       MSH6  103     R976H   
85       4       MSH6  104    E1322*   
86       1       MSH6  105    T1219I   
87       5       MSH6  106      G39E   
88       1       MSH6  108    R1076C   
89       5       MSH6  109    R1095H   
90       5       MSH6  111     V509A   
91       4       MSH6  112     E946*   
92       8      SF3B1  121     K700R   
93       9      SF3B1  122     R625C   
94       9      SF3B1  123     E622D   
95       9      SF3B1  124     H662Q   
96       9      SF3B1  125     R625D   
97       9      SF3B1  126     K666M   
98       9      SF3B1  127     H662R   
99   

In [138]:
data_all.iloc[3107,:]

Class                                                      NaN
Gene                                                    PIK3CA
ID                                                         281
Variation                                               T1025A
Text         Molecular genetic testing informs diagnosis, p...
Name: 3107, dtype: object

In [139]:
#Transform Amino Acid (AA) Letter to their three-letter abbreviation in order to find them in the text when they appear
One_to_Three_AA = {'C': 'Cys', 'D': 'Asp', 'S': 'Ser', 'Q': 'Gln', 'K': 'Lys',
         'I': 'Ile', 'P': 'Pro', 'T': 'Thr', 'F': 'Phe', 'N': 'Asn', 
         'G': 'Gly', 'H': 'His', 'L': 'Leu', 'R': 'Arg', 'W': 'Trp', 
         'A': 'Ala', 'V': 'Val', 'E': 'Glu', 'Y': 'Tyr', 'M': 'Met'}
pattern = re.compile('|'.join(One_to_Three_AA.keys()))

# Substitutions (subs)
## Functions for pre-processing of subs

In [140]:
# find_sub return the substituions that are in text and those that are not
def find_sub(data):    
    Boolean = [data.Variation[i][:-1] in data.Text[i] or #case 1.
               pattern.sub(lambda x: One_to_Three_AA[x.group()], data.Variation[i][:-1]) # case2
               in data.Text[i]  for i in data.index] ## because new indexing we use 
    
    sub_in_text = data[Boolean]
    not_Boolean = [not i for i in Boolean]  
    sub_not_in_text = data[not_Boolean]
    
    return sub_in_text, sub_not_in_text

# find_sub_numberChange searches for other number of a substitution i.e. G12V -> G_V because sometimes mistake in entry
# Is currently without One_to_three substitution or Variation[:-1] only the full variation
def find_sub_numberChange(data):
    Booleans = [] #will contain the different Booleans if found in text
    for i in data.index:
        split_variation = re.split('(\d+)', data.Variation[i]) # split based on a number
        first_Amino = re.escape(split_variation[0]) #re.escpae uses variable as regex
        last_Amino = re.escape(split_variation[-1])
        new_regex  = first_Amino + r"\d+" + last_Amino
        Boolean = bool(re.search(new_regex, data.Text[i]))
        Booleans.append(Boolean)
        
    sub_number_in_text = data[Booleans]
    not_Boolean = [not i for i in Booleans]  
    sub_number_no_text = data[not_Boolean]
    
    return sub_number_in_text, sub_number_no_text

# for substitutions that are still not found, use other keywords
def find_sub_pattern(data):    
    Boolean = [('mutat' in data.Text[i]) or ('variant' in data.Text[i]) or (data.Gene[i] in data.Text[i]) for i in data.index] ## because new indexing we use 
    
    sub_in_text = data[Boolean]
    not_Boolean = [not i for i in Boolean]  
    sub_not_in_text = data[not_Boolean]
    
    return sub_in_text, sub_not_in_text


In [141]:
##### get_sentences_sub use a window to extract sentences where the subs appear. 
# If window_left & window_right = 0 => just taking the sentences with subs

def get_sentences_sub(data, splitted_sentences):
    data.index = range(len(data)) #makes sure that index is right
    sentences_with_sub = [[] for _ in range(len(data))]
    for i in range(len(splitted_sentences)):
        sentences = splitted_sentences[i]
        one_to_three_variation = pattern.sub(lambda x: One_to_Three_AA[x.group()], data.Variation[i][:-1])
        Variation = data.Variation[i][:-1]    
        for j in range(len(sentences)):                              
            if (Variation in sentences[j]) or (one_to_three_variation in sentences[j]):
                new_regex = re.escape(Variation) + r"[\S]*" ###  r"[\S]*" because we look for Variation[:-1] not just Variation
                sentences[j] = re.sub(new_regex, ' placeholderMutation', sentences[j]) #case 1
                ### We add the space to ' placeholderMutation' because sometimes there are letters in front of it
                new_regex = re.escape(one_to_three_variation) + r"[\S]*"
                sentences[j] = re.sub(new_regex, ' placeholderMutation', sentences[j]) #case 2
                sentences_with_sub[i].extend(sentences[j:j+1])
                
    return sentences_with_sub

##### get_sentences_sub_number use a window to extract sentences where the subs appear that have different number i.e. G12V -> G_V

def get_sentences_sub_number(data, splitted_sentences):
    #position_sentences = [[] for _ in range(len(data))]  #### currently not used
    data.index = range(len(data))
    sentences_with_sub_number = [[] for _ in range(len(data))]
    for i in range(len(splitted_sentences)):
        sentences = splitted_sentences[i]
        split_variation = re.split('(\d+)', data.Variation[i]) # split based on a number
        first_Amino = re.escape(split_variation[0]) #re.escpae uses variable as regex
        last_Amino = re.escape(split_variation[-1])
        new_regex  = first_Amino + r"\d+" + last_Amino
        
        for j in range(len(sentences)):
            Boolean = bool(re.search(new_regex, sentences[j]))            
            if Boolean:
                sentences[j] = re.sub(new_regex, ' placeholderMutation', sentences[j]) # Again replacing the sentence with placeholder
                sentences_with_sub_number[i].extend(sentences[j:j+1])
    
    return sentences_with_sub_number

# for substitutions that are still not found, use other keywords
def get_sentences_pattern(data, splitted_sentences):
    data.index = range(len(data)) #makes sure that index is right
    sentences_with_sub = [[] for _ in range(len(data))]
    for i in range(len(splitted_sentences)):
        sentences = splitted_sentences[i]
        gene_name = data.Gene[i]
        for j in range(len(sentences)):                              
            if ('mutat' in sentences[j]) or ('variant' in sentences[j]) or (gene_name in sentences[j]):
                sentences[j] = re.sub(gene_name, ' placeholderGene', sentences[j]) # This time we replace for the gene because specific mutation not found
                sentences_with_sub[i].extend(sentences[j:j+1])               
    
    return sentences_with_sub

In [142]:
###### We use a window when sentences are too low. For 5 <= LENGTH <= 10: window of 1, for <= 5: window of 2 =, for 1 : window of 3
###### 

def get_window_sub(data, splitted_sentences, lengths):
    data.index = range(len(data)) #makes sure that index is right
    sentences_with_sub = [[] for _ in range(len(data))]
    for i in range(len(splitted_sentences)):
        sentences = splitted_sentences[i]
        length = lengths[i]
        if length == 1:
            window = 6
        elif length == 2:
            window = 3
        elif length >= 5:
            window=1
        else:
            window=2
        
        one_to_three_variation = pattern.sub(lambda x: One_to_Three_AA[x.group()], data.Variation[i][:-1])
        Variation = data.Variation[i][:-1] 
        all_sentences = []
        for j in range(len(sentences)):
            if (Variation in sentences[j]) or (one_to_three_variation in sentences[j]):
                new_regex = re.escape(Variation) + r"[\S]*" ###  r"[\S]*" because we look for Variation[:-1] not just Variation
                other_regex = re.escape(one_to_three_variation) + r"[\S]*"
                for sentence in sentences[max(j-window,0) : min(j+1+window, len(sentences)-1)]: # to account if start or end of text
                    sentence = re.sub(new_regex, ' placeholderMutation', sentence) #case 1
                    sentence = re.sub(other_regex, ' placeholderMutation', sentence) #case 2 after case 1
                    all_sentences.append(sentence)
        sentences_with_sub[i] = all_sentences
                    
    return sentences_with_sub

def get_window_sub_number(data, splitted_sentences, lengths):
    #position_sentences = [[] for _ in range(len(data))]  #### currently not used
    data.index = range(len(data))
    sentences_with_sub_number = [[] for _ in range(len(data))]
    for i in range(len(splitted_sentences)):
        sentences = splitted_sentences[i] 
        length = lengths[i]
        if length == 1:
            window = 6
        elif length == 2:
            window = 3
        elif length >= 5:
            window=1
        else:
            window=2
            
        split_variation = re.split('(\d+)', data.Variation[i]) # split based on a number
        first_Amino = re.escape(split_variation[0]) #re.escpae uses variable as regex
        last_Amino = re.escape(split_variation[-1])
        new_regex  = first_Amino + r"\d+" + last_Amino    
        
        all_sentences = []
        for j in range(len(sentences)):
            Boolean = bool(re.search(new_regex, sentences[j]))            
            if Boolean:
                for sentence in sentences[max(j-window,0) : min(j+1+window, len(sentences)-1)]:
                    sentence = re.sub(new_regex, ' placeholderMutation', sentence)
                    all_sentences.append(sentence)
        sentences_with_sub_number[i] = all_sentences
    
    return sentences_with_sub_number

def get_window_pattern(data, splitted_sentences, lengths):
    data.index = range(len(data)) #makes sure that index is right
    sentences_with_sub = [[] for _ in range(len(data))]
    for i in range(len(splitted_sentences)):
        sentences = splitted_sentences[i]
        length = lengths[i]
        if length == 1:
            window = 6
        elif length == 2:
            window = 3
        elif length >= 5:
            window=1
        else:
            window=2
        
        gene_name = data.Gene[i]
        all_sentences = []
        for j in range(len(sentences)):
            if ('mutat' in sentences[j]) or ('variant' in sentences[j]) or (gene_name in sentences[j]):
                for sentence in sentences[max(j-window,0) : min(j+1+window, len(sentences)-1)]: # to account if start or end of text
                    sentence = re.sub(gene_name, ' placeholderGene', sentence) #case 1
                    all_sentences.append(sentence)
        sentences_with_sub[i] = all_sentences
                    
    return sentences_with_sub




In [143]:
#### Converts list of sentences into one string of sentences for each document => to use for tfidf etc.
def sentences_to_string(sentences_list):
    sentence_strings = []
    for sentences in sentences_list:
        sentence_string =  ' '.join(str(sentence) for sentence in sentences)
        sentence_strings.append(sentence_string)
    
    return sentence_strings 

## Subs processing of the data set 

In [146]:
######### First find those that have the format of being a substitution in data
data_all['Substitutions_var'] = data_all.Variation.apply(lambda x: bool(re.search('^[A-Z]\\d+[A-Z*]$', x))*1) #multiplying by 1 converts True to 1, False to 0 => Maybe modify this later?
data_all['null'] = data_all.Variation.apply(lambda x: bool(re.search('null', x))*1)
data_all = data_all[(data_all['Substitutions_var']==1) | (data_all['null']==1) ] ### Now we know the index of where a substitution occurs - the data_sub
data_all = data_all.loc[:, 'Class':'Text']
data_sub = data_all
print("Length of total subs: %i" %len(data_sub)) # other ways to process it like finding the word 'mutation' 
data_all

Length of total subs: 3544


Class       Gene   ID Variation  \
0        2        CBL    1     W802*   
1        2        CBL    2     Q249E   
2        3        CBL    3     N454D   
3        4        CBL    4     L399V   
4        4        CBL    5     V391I   
5        5        CBL    6     V430M   
6        4        CBL    8     Y371H   
7        4        CBL    9     C384R   
8        4        CBL   10     P395A   
9        4        CBL   11     K382E   
10       4        CBL   12     R420Q   
11       4        CBL   13     C381A   
12       5        CBL   14     P428L   
13       4        CBL   15     D390Y   
14       4        CBL   17     Q367P   
15       5        CBL   18     M374V   
16       4        CBL   19     Y371S   
17       6        CBL   20      H94Y   
18       4        CBL   21     C396R   
19       4        CBL   22     G375P   
20       4        CBL   23     S376F   
21       4        CBL   24     P417A   
22       4        CBL   25     H398Y   
23       4      SHOC2   26       S2G   
24       4       TERT   27     Y846C   
25       7       TERT   28     C228T   
26       4       TERT   29     H412Y   
27       4       TERT   30     H876Q   
28       4       TERT   32     P704S   
29       7       TERT   34     C250T   
30       4     DICER1   35    G1809R   
31       4     DICER1   36    G1809K   
32       1     DICER1   37    D1709E   
33       1     DICER1   38    D1709A   
34       4     DICER1   39    E1705A   
35       4     DICER1   40    D1810A   
36       4     DICER1   42    E1705K   
37       4      PTPRT   44    T1365M   
38       1      PTPRT   45     V648G   
39       4      PTPRT   46     T844M   
40       1      PTPRT   47     A707T   
41       4      PTPRT   49    R1343L   
42       1      PTPRT   50     A209T   
43       1      PTPRT   51     Y280H   
44       4      PTPRT   52     D927G   
45       1      PTPRT   53     N510K   
46       1      PTPRT   54     F248S   
47       1      PTPRT   55     L708P   
48       4      PTPRT   56     V995M   
49       1      PTPRT   57     Y412F   
50       1      PTPRT   58      F74S   
51       1      PTPRT   59    R1040L   
52       1      PTPRT   60     R453C   
53       4      PTPRT   61    R1209W   
54       4      PTPRT   62    A1022E   
55       4      PTPRT   63     Q984K   
56       1      PTPRT   64     T605M   
57       1      PTPRT   65     K218T   
58       4      PTPRT   66    N1125I   
59       7       RHEB   67      Y35C   
60       7       RHEB   68      Y35N   
61       7       RHEB   69      Y35H   
62       4      RAD50   73    L1273F   
63       2      CCND3   76     P284L   
64       7      CCND3   77     Q276*   
65       7      CCND3   78     T286A   
66       7      CCND3   79     T283A   
67       2      CCND3   80     I290A   
68       2      CCND3   81     I290R   
69       7       RIT1   82      A77S   
70       7       RIT1   83      A77P   
71       2       RIT1   84      A77T   
72       7       RIT1   85      M90I   
73       4     TGFBR1   89      N45S   
74       1     TGFBR1   90     R487Q   
75       4     TGFBR1   91      C41Y   
76       4     TGFBR1   92      G52R   
77       4     TGFBR1   93      P83L   
78       1     TGFBR1   94     S241L   
79       4     TGFBR1   95     S387Y   
80       2     TGFBR2   97     R537P   
81       4     TGFBR2   98     D404G   
82       4     TGFBR2   99     P525L   
83       4       MSH6  102     R922*   
84       1       MSH6  103     R976H   
85       4       MSH6  104    E1322*   
86       1       MSH6  105    T1219I   
87       5       MSH6  106      G39E   
88       1       MSH6  108    R1076C   
89       5       MSH6  109    R1095H   
90       5       MSH6  111     V509A   
91       4       MSH6  112     E946*   
92       8      SF3B1  121     K700R   
93       9      SF3B1  122     R625C   
94       9      SF3B1  123     E622D   
95       9      SF3B1  124     H662Q   
96       9      SF3B1  125     R625D   
97       9      SF3B1  126     K666M   
98       9      SF3B1  127     H662R   
99   

### Subs inside the text

#### Subs inside the text: all sentences

In [147]:
## First consider the subs that appear in text
sub_text, sub_no_text = find_sub(data_sub) 

In [148]:
## use tokenizer to split into sentences of all the subs in text 
NLTK_sub = [sent_tokenize(sub_text.Text[i]) for i in sub_text.index] 

In [149]:
NLTK_window = copy.deepcopy(NLTK_sub) # a deep copy is necessary besauce something magical and strange happening without it
NLTK_copy = copy.deepcopy(NLTK_sub) # again for backup purposes

In [150]:
# extract window for the sub sentences where they appear
# !! Use [:] because it makes a copy and doesn't change anything to the original indexes
sub_sentences = get_sentences_sub(sub_text[:], NLTK_copy[:]) # choosing for window 0 as default now
sub_sentences_string = sentences_to_string(sub_sentences)

In [151]:
# Replace text in data_all
data_all.Text.loc[sub_text.index] = sub_sentences_string
data_all.Text.loc[sub_text.index]

0       Using select c-CBL somatic mutations such as S...
1       Using select c-CBL somatic mutations such as S...
2       Most of the changes were novel, although 4 cas...
3       Finally, the third group constituted mutations...
4       Finally, the third group constituted mutations...
5       The second group of mutants (M374V,  placehold...
6       We investigated the mechanism by which CBL- pl...
7       We investigated the mechanism by which CBL-Y37...
8       Finally, the third group constituted mutations...
9       Purified PCR amplicons (CBLWT, CBLC381A, CBL p...
10      Purified PCR amplicons (CBLWT, CBLC381A, CBLK3...
11      Purified PCR amplicons (CBLWT, CBL placeholder...
12      The second group of mutants (M374V, V430M,  pl...
13      Purified PCR amplicons (CBLWT, CBLC381A, CBLK3...
14      When introduced into Lin- Sca1+ c-Kit+ (LSK) H...
15      The second group of mutants ( placeholderMutat...
16      When introduced into Lin- Sca1+ c-Kit+ (LSK) H...
17      Using 

#### Subs inside the text: sentences with length <=10

In [152]:
######### We rerun for window. Length<2 : w = 3, Length >=6: w = 1, Length in between: w = 2
indexes = [index for index, sentences in enumerate(sub_sentences) if len(sentences) <= 10]
sentence_lengths = [len(sentences) for index, sentences in enumerate(sub_sentences) if len(sentences) <= 10]
NLTK_sub_window = [NLTK_window[i] for i in indexes]

In [153]:
new_index = sub_text.index[indexes]
sub_window = sub_text.loc[new_index] # gets the subs with the low length
sub_window #1524 cases 

Class      Gene    ID Variation  \
2        3       CBL     3     N454D   
3        4       CBL     4     L399V   
4        4       CBL     5     V391I   
5        5       CBL     6     V430M   
8        4       CBL    10     P395A   
12       5       CBL    14     P428L   
14       4       CBL    17     Q367P   
15       5       CBL    18     M374V   
16       4       CBL    19     Y371S   
18       4       CBL    21     C396R   
19       4       CBL    22     G375P   
20       4       CBL    23     S376F   
21       4       CBL    24     P417A   
22       4       CBL    25     H398Y   
24       4      TERT    27     Y846C   
26       4      TERT    29     H412Y   
27       4      TERT    30     H876Q   
28       4      TERT    32     P704S   
32       1    DICER1    37    D1709E   
33       1    DICER1    38    D1709A   
34       4    DICER1    39    E1705A   
35       4    DICER1    40    D1810A   
36       4    DICER1    42    E1705K   
38       1     PTPRT    45     V648G   
40       1     PTPRT    47     A707T   
42       1     PTPRT    50     A209T   
43       1     PTPRT    51     Y280H   
45       1     PTPRT    53     N510K   
46       1     PTPRT    54     F248S   
47       1     PTPRT    55     L708P   
48       4     PTPRT    56     V995M   
49       1     PTPRT    57     Y412F   
50       1     PTPRT    58      F74S   
51       1     PTPRT    59    R1040L   
52       1     PTPRT    60     R453C   
54       4     PTPRT    62    A1022E   
56       1     PTPRT    64     T605M   
57       1     PTPRT    65     K218T   
63       2     CCND3    76     P284L   
64       7     CCND3    77     Q276*   
68       2     CCND3    81     I290R   
69       7      RIT1    82      A77S   
70       7      RIT1    83      A77P   
72       7      RIT1    85      M90I   
73       4    TGFBR1    89      N45S   
75       4    TGFBR1    91      C41Y   
77       4    TGFBR1    93      P83L   
78       1    TGFBR1    94     S241L   
86       1      MSH6   105    T1219I   
93       9     SF3B1   122     R625C   
94       9     SF3B1   123     E622D   
95       9     SF3B1   124     H662Q   
96       9     SF3B1   125     R625D   
97       9     SF3B1   126     K666M   
98       9     SF3B1   127     H662R   
99       9     SF3B1   128     R625H   
101      9     SF3B1   130     R625L   
102      9     SF3B1   131     E622Q   
103      9     SF3B1   132     R625G   
104      9     SF3B1   133     K666N   
105      9     SF3B1   134     K666R   
114      2      EGFR   153     L858M   
118      2      EGFR   157     T710A   
120      2      EGFR   159     E709V   
125      7      EGFR   167     A864T   
130      2      EGFR   177     R836C   
132      2      EGFR   179     G857E   
136      2      EGFR   183     L692F   
138      2      EGFR   186     E746V   
141      6      EGFR   191     S921R   
142      2      EGFR   192     N826Y   
143      3      EGFR   196     C628Y   
147      7      EGFR   202     N826S   
149      7      EGFR   207     R108K   
151      2      EGFR   209     S645C   
156      4      EGFR   217     K745M   
162      7      EGFR   227     S784F   
163      7      EGFR   228     Y801H   
166      2      EGFR   234     L703P   
168      4      EGFR   237     E866K   
169      7      EGFR   241     E734Q   
171      7      EGFR   243     T263P   
172      7      EGFR   244     T785A   
174      7      EGFR   246     L838V   
175      2      EGFR   247     P753S   
177      4      EGFR   250     I853T   
180      2      EGFR   253     V769M   
181      7      EGFR   254     W731L   
187      7      EGFR   263     R776C   
188      7      EGFR   264     E868G   
192      2      EGFR   269     E709G   
194      2      EGFR   271     P596L   
197      7      EGFR   274     G863D   
200      2      EGFR   278     G465E   
202      1  HIST1H1C   290     S102F   
208      4     CHEK2   298     E321K   
209      3   TMPRSS2   303      T75M   
214      1      ELF3   309     I279P   
215      1      ELF3   310     R331P   
216  

In [154]:
sub_window_sentences = get_window_sub(sub_window[:], NLTK_sub_window[:], sentence_lengths) 
sub_window_sentences = [sorted(set(sentences), key = sentences.index) for sentences in sub_window_sentences] # removes duplicates
sub_window_string = sentences_to_string(sub_window_sentences)

In [155]:
sub_window_sentences[3] # only thing we can do about sentences like this one is look at the full text words now

['Figure 4 Figure 4 Structures of wild type (green) and K382E mutant (tan) are shown for nCBL and pCBL-E2-S states.',
 'Salt bridges are shown as dashed lines and in both cases mutation affects the stability by disrupting the salt bridge.',
 'The second group of mutants (M374V,  placeholderMutation P428L, Q249E and double mutant S80N/H94Y) maintained the CBL activity equivalent to or greater than wild-type CBL (relative densitometry of 80% or higher) (Fig.',
 '3B).',
 'Consistent with this, the levels of the activated EGFR were also decreased in these samples (Fig.',
 'Two of these CBL mutants resulted in more ubiquitination of EGFR compared to wild type CBL.',
 'For example, the Q249E mutant showed an increased ubiquitination of EGFR in 293T and HeLa cells while the M374V mutant resulted in higher ubiquitination levels in A549 and HeLa cells (Figure 3 and S6).',
 'Only  placeholderMutation mutant was on the borderline with the densitometry ratio of 0.8.',
 'All mutations from the seco

In [156]:
# Finally: replacing those texts in data_all
data_all.Text.loc[new_index] = sub_window_string
data_all.Text.loc[new_index]

2       View inlineView popup Table 2 Cases analyzed f...
3       For example, the Q249E mutant showed an increa...
4       For example, the Q249E mutant showed an increa...
5       Figure 4 Figure 4 Structures of wild type (gre...
8       For example, the Q249E mutant showed an increa...
12      Moreover, K382E mutation had a significant imp...
14      Transformed NIH3T3 cells showed PI3 kinase-dep...
15      Figure 4 Figure 4 Structures of wild type (gre...
16      Transformed NIH3T3 cells showed PI3 kinase-dep...
18      Figure 3 Figure 3 (A) EGFR ubiquitination. HEK...
19      For example, the Q249E mutant showed an increa...
20      Figure 6 Download figureOpen in new tabDownloa...
21      We fully sequenced the coding exons of these g...
22      Overall survival (A) and progression-free surv...
24      Both families contain compound heterozygotes. ...
26      Here we describe 2 families in which 2 TERT mu...
27      Both families contain compound heterozygotes. ...
28      Both f

### Subs with a different number inside the text

#### Subs with a different number inside the text: all sentences


In [157]:
# now the subs that don't appear in text: one reason is different number in the substitution. f.e. G12V -> G13V 
sub_number_text, sub_number_no_text = find_sub_numberChange(sub_no_text) # 131 cases with number change

In [158]:
## use tokenizer to split into sentences of subs that have different number in text 
NLTK_sub_number = [sent_tokenize(sub_number_text.Text[i]) for i in sub_number_text.index]
NLTK_sub_number_window = copy.deepcopy(NLTK_sub_number) # a deep copy is necessary besauce something magical and strange happening without it
NLTK_sub_number_copy = copy.deepcopy(NLTK_sub_number) # again for backup purposes

In [159]:
# extract window for the sub sentences where they appear
# !! Use [:] because it makes a copy and doesn't change anything to the original indexes
sub_number_sentences = get_sentences_sub_number(sub_number_text[:], NLTK_sub_number_copy[:])
sub_number_string = sentences_to_string(sub_number_sentences)

In [160]:
data_all.Text.loc[sub_number_text.index] = sub_number_string #iloc for indexing based on integers
data_all.Text.loc[sub_number_text.index]

37      His-tagged versions of the catalytic region of...
41      His-tagged versions of the catalytic region of...
53      His-tagged versions of the catalytic region of...
55      His-tagged versions of the catalytic region of...
58      His-tagged versions of the catalytic region of...
62      While both were missense mutations, in silico ...
150      placeholderMutation and T847I were also found...
153     Complex mutation  placeholderMutation and dele...
191     As a positive control, we introduced the well-...
198     And in the series of Pallis and colleagues (12...
211     Recurrent mutations in H3F3A, which encodes th...
212     Histone H3-K42me2 may regulate transcription  ...
213     Recurrent mutations in H3F3A, which encodes th...
394     Both combinations contained mutations of codon...
474     In the present study, we have focused on two d...
494     Such mutant amino acid specificity was also ap...
578     In contrast, ectopic expression of FGFR4  plac...
823     Recent

#### Subs with a different number inside the text: sentences with length <= 10

In [161]:
######### ######### We rerun for window. Length<2 : w = 3, Length >=6: w = 1, Length in between: w = 2
indexes = [index for index, sentences in enumerate(sub_number_sentences) if len(sentences) <= 10]
sentence_lengths = [len(sentences) for index, sentences in enumerate(sub_number_sentences) if len(sentences) <= 10]
NLTK_window = [NLTK_sub_number[i] for i in indexes]

In [162]:
new_index = sub_number_text.index[indexes]
sub_number_window = sub_number_text.loc[new_index] # gets the subs with the low length
sub_number_window #87 cases 

Class    Gene    ID Variation  \
37       4   PTPRT    44    T1365M   
41       4   PTPRT    49    R1343L   
53       4   PTPRT    61    R1209W   
150      2    EGFR   208     V774A   
153      2    EGFR   213     V774M   
191      7    EGFR   267     G810S   
198      2    EGFR   275     L838P   
213      8   H3F3A   308      G35V   
394      4    TP53   521     E286K   
494      1   FBXW7   632     G423R   
578      5   ERBB2   730     V750E   
825      9    EZH2  1083     Y646H   
827      9    EZH2  1085     Y646S   
830      6    RXRA  1091     S247F   
831      6    RXRA  1092     S247Y   
862      2     MET  1139    D1010N   
865      2     MET  1144    H1106D   
869      7     MET  1149    N1100Y   
936      2  PIK3CB  1228    E1051K   
967      5  PIK3R2  1276     S273C   
994      6    MLH1  1305     P654L   
1005     1    MLH1  1316      G67R   
1011     4    MLH1  1322     P648L   
1097     5   FGFR3  1428     N653H   
1130     7   FGFR2  1466     N549S   
1140     7   FGFR2  1478     M535I   
1145     7   FGFR2  1486     L617M   
1147     2   FGFR2  1489     K641N   
1155     2   FGFR2  1499     K659E   
1206     3     ALK  1562    R1231Q   
1529     7  CARD11  1943     S250P   
1598     7  MAP2K1  2024     E144K   
1648     1    AGO2  2086     R647A   
1649     1    AGO2  2087     R583A   
1655     1   CDK12  2099     K765R   
1658     1   CDK12  2103     D887N   
1726     4    PTEN  2193      R15K   
1829     7    JAK1  2312    G1079D   
1917     1   BRCA1  2422    G1803A   
1931     1   BRCA1  2436    M1689T   
1964     1   BRCA1  2470    S1715C   
1975     1   BRCA1  2482    L1705P   
2003     1   BRCA1  2510    S1841N   
2070     1   BRCA1  2579    G1763V   
2112     4   BRCA1  2622    S1722F   
2126     5   BRCA1  2636    R1751Q   
2146     5   BRCA1  2656    M1663K   
2190     2    BRAF  2705     N581S   
2198     7    BRAF  2723     G464R   
2201     3    BRAF  2727     R462I   
2205     5    BRAF  2732     I463S   
2221     7    BRAF  2756     E586K   
2254     6   BRCA2  2790    L2106P   
2279     6   BRCA2  2815    K2472T   
2280     6   BRCA2  2816    S1670A   
2301     6   BRCA2  2837    S2483N   
2380     7  NFE2L2  2919      G81D   
2471     7  NOTCH1  3065    I1616N   
2472     7  NOTCH1  3067    R1598P   
2474     7  NOTCH1  3070    L1596H   
2477     7  NOTCH1  3074    I1680N   
2479     7  NOTCH1  3076    A1701P   
2482     5  NOTCH1  3080    R1608S   
2483     7  NOTCH1  3082    I1616T   
2484     7  NOTCH1  3083    V1676D   
2488     7  NOTCH1  3090    F1592S   
2490     7  NOTCH1  3092    V1576E   
2594     7     RET  3261     C634R   
2597     7     RET  3265     C611Y   
2618     7     RET  3288     C630R   
2622     7     RET  3292     C634Y   
2769     4     NF1  2487    K1423E   
2834     7  NOTCH1  3574    I1718T   
2932   NaN   ERBB2    15     G746S   
2952   NaN   SMAD4    43     G386C   
2954   NaN   ERBB2    47     V762M   
3008   NaN   SMAD4   132     G386S   
3045   NaN   ERBB2   187     D739Y   
3104   NaN    TP53   278     V173G   
3197   NaN   EPHA5   431     G583E   
3222   NaN  CRNKL1   465     S116F   
3251   NaN    IDH2   510     R120M   
3258   NaN  CDKN2A   519      A97V   
3304   NaN    EGFR   602     A289T   
3369   NaN  CTNNB1   710      G34R   
3443   NaN   ERBB2   832     S280Y   
3453   NaN   STK33   852     F136L   

                                                   Text  
37    Tyrosine phosphorylation, regulated by protein...  
41    Tyrosine phosphorylation, regulated by protein...  
53    Tyrosine phosphorylation, regulated by protein...  
150   Purpose: Clinical features of epidermal growth...  
153   Purpose: Clinical features of epidermal growth...  
191   Purpose: Epidermal growth factor receptor (EGF...  
198   Purpose: Clinical features of epidermal growth...  
213   The DNA entry and exit points on the nucleosom...  
394   The transcription factor and tumor suppressor ...  
494   Background  Melanoma is a heterogeneous tumor ...  
578   We assessed soma

In [163]:
sub_window_sentences = get_window_sub_number(sub_number_window[:], NLTK_window[:], sentence_lengths) 
sub_window_sentences = [sorted(set(sentences), key = sentences.index) for sentences in sub_window_sentences] # removes duplicates
sub_window_string = sentences_to_string(sub_window_sentences)
sub_window_sentences[24]

['Modeling of the pathogenic mutations was performed and analyzed using O [39].',
 'Atomic superimpositions were performed using program lsqkab [40] in CCP4 Suite [41] and structural representations were prepared using PyMol [42].',
 'Protein Expression and Purification The cDNA fragment encoding residues P459 to E769 of human FGFR2c (Accession code: NP_075259) was amplified by polymerase chain reaction and subcloned into pET bacterial expression vector with an NH2 terminal 6× His tag to aid in protein purification.',
 'Point mutations (M536I, M538I, I548V, N550H, N550K,  placeholderMutation, V565I, E566G, L618M, and K660E) were introduced using QuikChange Site-Directed Mutagenesis Kit (Stratagene, La Jolla, CA).',
 'The bacterial strain BL21 (DE3) cells were transformed with the expression constructs, and kinase expression was induced with 1 mM isopropyl-L-thio-BDgalactopyranoside overnight at the appropriate temperature.',
 'The cells were lysed, and the soluble kinase proteins were 

In [164]:
data_all.Text.loc[new_index] = sub_window_string
data_all.Text.loc[new_index]

37      Second, the prevalence of mutations in the cod...
41      Second, the prevalence of mutations in the cod...
53      Second, the prevalence of mutations in the cod...
150     Some other uncommon EGFR mutations, that is, t...
153     By searching the database (38), we found that ...
191     To test more directly whether the mutations EG...
198     However, case numbers were small in previous s...
213     Somatic mutations in the H3.3-ATRX-DAXX chroma...
394     1. The effect of suppressor amino acid changes...
494     Examining the spectrum of KRAS mutations, whic...
578     None of the somatic alleles of EPHA3, ERBB4, F...
825     Trimethylation of H3K27 is a mechanism for sup...
827     EZH2 is the catalytic subunit of the PRC2 comp...
830     1b have not previously been reported as statis...
831     1b have not previously been reported as statis...
862     Summary During the past decade, the treatment ...
865     The H1112 mutations were immediately adjacent ...
869     Mutati

In [165]:
data_all.loc[len(new_train):].Text[data_all.loc[len(new_train):].index[4]]

'We amplified all of the coding exons from 24 primary ESCC tumors and 16 tumor cell lines. We found three mutations in three ESCC primary tumors (Fig. 2 ⇓ ; Table 2 ⇓ ) and one mutation in a tumor cell line (Table 2) ⇓ . The amino acid changes in the mutations were R102K, A242T,  placeholderMutation and S623N. We also analyzed the blood DNAs from the three patients with mutations in the RNF6 gene, and all contained the wild-type allele (Fig. 2) ⇓ , thus indicating that the mutations in the ESCC primary tumors were acquired during tumorigenesis in somatic cells. RNF6 contains three domains: an arginine domain (amino acids 292–424), a poly-aspartic acid domain (amino acids 598–601), and a Zinc finger domain (amino acids 632–673). The mutation S623N, which is located near the Zinc finger domain, may affect its DNA-binding activity. Both A242T and  placeholderMutation may perturb the structure and function of the RNF6 protein. In the first case, the side chain of amino acid Thr is larger t

#### Subs that are still not found: all sentences

In [166]:
sub_number_no_text.shape # 365 left

(365, 5)

In [167]:
sub_number_no_text.loc[len(new_train):].shape # 62 in test

(62, 5)

In [168]:
texts_to_analyze = list(sub_number_no_text.loc[len(new_train):].Text)

In [169]:
len(set(texts_to_analyze)) # basically 31 texts the same!

31

In [170]:
texts_to_analyze[8]

"Ongoing cancer genome characterization studies continue to elucidate the spectrum of genomic abnormalities that drive many cancers, and in the clinical arena assessment of the driver genetic alterations in patients is playing an increasingly important diagnostic and/or prognostic role for many cancer types. However, the landscape of genomic abnormalities is still unknown for less common cancers, and the influence of specific genotypes on clinical behavior is often still unclear. To address some of these deficiencies, we developed Profile, a prospective cohort study to obtain genomic information on all patients at a large tertiary care medical center for cancer-related care. We enrolled patients with any cancer diagnosis, and, for each patient (unselected for cancer site or type) we applied mass spectrometric genotyping (OncoMap) of 471 common recurrent mutations in 41 cancer-related genes. We report the results of the first 5000 patients, of which 26% exhibited potentially actionable 

In [171]:
sub_number_no_text.loc[len(new_train):] # A lot of sentences starting with 'Among...'

Class    Gene   ID Variation  \
2933   NaN    TP53   16     Y234S   
2937   NaN   CSF1R   20     Y969H   
2944   NaN    SYT6   31     A406T   
2949   NaN   CSF1R   38     Y969F   
2962   NaN   STK11   58     G163C   
2979   NaN     DCC   87    P1375H   
2990   NaN   ACVR1  104     R258M   
3018   NaN   STK11  144      R86G   
3026   NaN    AKT2  156     S302G   
3030   NaN     MYC  161      P58L   
3033   NaN    TP53  165     S241A   
3053   NaN   SF3B2  201     E700G   
3068   NaN    XPO1  224     E571V   
3073   NaN    TP53  229     R282P   
3085   NaN  CTNNB1  251      S37P   
3089   NaN    TP53  255     R249T   
3091   NaN   CSF1R  258     L301S   
3107   NaN  PIK3CA  281    T1025A   
3135   NaN  CTNNB1  326      T40A   
3150   NaN     MCC  350     A888V   
3177   NaN   FGFR2  396     N639K   
3180   NaN    PTEN  403     R159S   
3191   NaN   ERBB2  422     L755M   
3192   NaN     MCC  423     R696Q   
3195   NaN    ASS1  426      S18L   
3198   NaN    KRAS  433     A146P   
3207   NaN    EGFR  443     E749Q   
3210   NaN   STK11  447     Q123R   
3220   NaN   ERBB2  463     N827S   
3227   NaN    TP53  471     R148I   
3231   NaN  NOTCH1  480    D1642H   
3254   NaN  NOTCH1  515    R2327W   
3257   NaN    TP53  518      S83I   
3269   NaN    TP53  536     Y234N   
3275   NaN   CSF1R  546     Y969C   
3285   NaN   CSF1R  567     L301F   
3298   NaN    TP53  591     V173A   
3300   NaN   SMAD4  593     R361P   
3303   NaN  CDKN2A  601      A97G   
3320   NaN    TP53  628     T125P   
3327   NaN   FGFR2  643     C383Y   
3334   NaN     MYC  660      T73P   
3340   NaN    XPO1  668     E571A   
3374   NaN     DCC  720     M168T   
3375   NaN   STK11  721     S216F   
3405   NaN   SMAD4  770     R361H   
3408   NaN    TP53  776     Y220D   
3423   NaN   STK19  797      D89N   
3424   NaN    EGFR  798     R108G   
3425   NaN    EGFR  800     S752Y   
3426   NaN   MED12  801    L1224V   
3434   NaN   FGFR2  816     Y382H   
3459   NaN   FGFR2  861     I548L   
3460   NaN    TP53  862     S109P   
3471   NaN   STK11  878     G196V   
3476   NaN    TP53  889     Y104C   
3480   NaN  ABCB11  896     E297G   
3485   NaN    TP53  902     T125R   
3497   NaN    TP53  920      L35F   
3515   NaN  PIK3CA  946     D549N   
3529   NaN    TP53  971     S109Y   
3531   NaN    TP53  973     R280G   

                                                   Text  
2933  Among the best-studied therapeutic targets in ...  
2937  The FMS gene encodes the functional cell surfa...  
2944  The phosphatidylinositol-3-kinase (PI3K)/serin...  
2949  Clinical characteristics.Adult-onset leukoence...  
2962  Germline mutation in serine/threonine kinase 1...  
2979  DCC is a candidate tumor-suppressor gene encod...  
2990  Among the best-studied therapeutic targets in ...  
3018  Germline mutation in serine/threonine kinase 1...  
3026  Ongoing cancer genome characterization studies...  
3030  Among the best-studied therapeutic targets in ...  
3033  Among the best-studied therapeutic targets in ...  
3053  Among the best-studied therapeutic targets in ...  
3068  Among the best-studied therapeutic targets in ...  
3073  Among the best-studied therapeutic targets in ...  
3085  Among the best-studied therapeutic targets in ...  
3089  Among the best-studied therapeutic targets in ...  
3091  The FMS gene encodes the functional cell surfa...  
3107  Molecular genetic testing informs diagnosis, p...  
3135  Ongoing cancer genome characterization studies...  
3150  STUDIES OVER THE PAST SEVERAL  years have allo...  
3177  Among the best-studied therapeutic targets in ...  
3180  Rapamycin is a natural product macrolide that ...  
3191  Among the best-studied therapeutic targets in ...  
3192  STUDIES OVER THE PAST SEVERAL  years have allo...  
3195  Point mutations of the Bcr-Abl kinase domain (...  
3198  The epidermal growth factor receptor (EGFR) is...  
3207  Epidermal growth factor receptor (EGFR) mutati...  
3210  Germline mutation in serine/threonine kinas

In [172]:
# subs that are still not found, look based on a pattern like the word 'mutat', 'variat' or the gene in text
sub_pattern_text, sub_pattern_no_text = find_sub_pattern(sub_number_no_text) # 

In [173]:
sub_pattern_no_text # only 13 texts that still don't include the sentences of which three nulls and low text_words length, replace with nulls

Class    Gene    ID Variation  \
108      5    EGFR   140     I491M   
111      2    EGFR   145     K467T   
185      2    EGFR   259     S464L   
292      4    TP53   416     P151S   
841      1   FANCA  1109    S1088F   
1078     6   FGFR3  1407     K508M   
1255     4     VHL  1613     L158Q   
1524     7  CARD11  1936     G116S   
1528     7  CARD11  1942     E127G   
1820     7    JAK1  2302     R724H   
1827     7    JAK1  2309     R879C   
2220     7    BRAF  2755     G596C   
2427     2     KIT  2980     N655K   

                                                   Text  
108   The accurate determination of perfluoroalkyl s...  
111   The accurate determination of perfluoroalkyl s...  
185   The accurate determination of perfluoroalkyl s...  
292   The effects of chlorpromazine on various prope...  
841                                                null  
1078                                               null  
1255  The case of a 40-year-old woman with severe ed...  
1524  Left ventricular (LV) remodeling is a signific...  
1528  Left ventricular (LV) remodeling is a signific...  
1820  Regulatory T (T reg) cells have a major role i...  
1827  Regulatory T (T reg) cells have a major role i...  
2220                                               null  
2427  TO THE EDITOR: I commend Drs. Freeman and Bank...

In [174]:
data_all.Text.loc[sub_pattern_no_text.index] = ''
data_all.Text.loc[sub_pattern_no_text.index]

108     
111     
185     
292     
841     
1078    
1255    
1524    
1528    
1820    
1827    
2220    
2427    
Name: Text, dtype: object

In [175]:
## use tokenizer to split into sentences of subs that have keywords or gene
NLTK_sub_pattern = [sent_tokenize(sub_pattern_text.Text[i]) for i in sub_pattern_text.index]

In [176]:
# !! Use [:] because it makes a copy and doesn't change anything to the original indexes
sub_pattern_sentences = get_sentences_pattern(sub_pattern_text[:], NLTK_sub_pattern[:])
sub_pattern_string = sentences_to_string(sub_pattern_sentences)

In [177]:
data_all.Text.iloc[sub_pattern_text.index] = sub_pattern_string #iloc for indexing based on integers
data_all.Text.iloc[sub_pattern_text.index]

39      Mutations in CBL, encoding an E3 ubiquitin lig...
67      This D1 domain contains only two serine residu...
83      Identification of a high-risk disease-causing ...
85      In this study, we profiled 70 colorectal cance...
87      Identification of a high-risk disease-causing ...
88      Most Lynch Syndrome-associated CRCs are report...
90      Identification of a high-risk disease-causing ...
91      Germ-line  placeholderGene mutations, which ar...
107     The  placeholderGene gene encodes subunit 1 of...
113     Purpose: Mutations in epidermal growth factor ...
116     Clinical data and epidermal growth factor rece...
122     Clinical data and epidermal growth factor rece...
126     Mutations in the epidermal growth factor recep...
131     In selected patients with advanced non-small c...
135     Purpose: Clinical reports about responsiveness...
137     ‘Classical' mutations in the  placeholderGene ...
154     Purpose: Clinical features of epidermal growth...
159     Introd

#### Subs that are still not found inside the text: sentences with length <= 10

In [178]:
######### ######### We rerun for window. Length<2 : w = 3, Length >=6: w = 1, Length in between: w = 2
indexes = [index for index, sentences in enumerate(sub_pattern_sentences) if len(sentences) <= 10]
sentence_lengths = [len(sentences) for index, sentences in enumerate(sub_pattern_sentences) if len(sentences) <=10]
NLTK_window = [NLTK_sub_pattern[i] for i in indexes]

In [179]:
sentence_lengths # 19 cases where we still look again, some of them from same text

[4, 4, 4, 4, 2, 2, 3, 5, 5, 5, 5, 3, 4, 5, 5, 5, 5, 5, 9]

In [180]:
new_index = sub_pattern_text.index[indexes]
sub_pattern_window = sub_pattern_text.loc[new_index] # gets the subs with the low length
sub_pattern_window #87 cases 

Class    Gene    ID Variation  \
67       2   CCND3    80     I290A   
231      4    CDH1   344     A617T   
233      4    CDH1   346     A634V   
235      4    CDH1   348     T340A   
450      1   SMAD4   581     R378A   
461      1   SMAD4   593     D493A   
505      4  CDKN2A   648      Q50*   
543      4  CDKN2A   688      R79P   
547      4  CDKN2A   692      G93W   
548      4  CDKN2A   693     V118D   
664      4   ERCC4   833     E875G   
1226     4    PMS1  1583     Q233*   
1997     6   BRCA1  2504      V11A   
2363     1     NF2  2900     E106G   
2368     1     NF2  2906     Q538P   
2370     5     NF2  2908     Q324L   
2685     4    MSH2   859     R621*   
2814     4  CDKN2A  3322      P73L   
2979   NaN     DCC    87    P1375H   

                                                   Text  
67    The activities of cyclin D-dependent kinases s...  
231   E-cadherin is involved in the formation of cel...  
233   E-cadherin is involved in the formation of cel...  
235   E-cadherin is involved in the formation of cel...  
450   The formation of protein complexes between pho...  
461   The formation of protein complexes between pho...  
505   The p16 gene is located in chromosome 9p21, a ...  
543   Cell division is controlled by a series of pos...  
547   Cell division is controlled by a series of pos...  
548   Cell division is controlled by a series of pos...  
664   In addition to its well-documented effects on ...  
1226  HEREDITARY nonpolyposis colorectal cancer (HNP...  
1997   Identification of protein-protein interaction...  
2363  Neurofibromatosis 2 (NF2) is a tumor predispos...  
2368  Neurofibromatosis 2 (NF2) is a tumor predispos...  
2370  Neurofibromatosis 2 (NF2) is a tumor predispos...  
2685  Hereditary nonpolyposis colon cancer (HN-PCC) ...  
2814  Cell division is controlled by a series of pos...  
2979  DCC is a candidate tumor-suppressor gene encod...

In [181]:
sub_window_sentences = get_window_pattern(sub_pattern_window[:], NLTK_window[:], sentence_lengths) 
sub_window_sentences = [sorted(set(sentences), key = sentences.index) for sentences in sub_window_sentences] # removes duplicates
sub_window_string = sentences_to_string(sub_window_sentences)

In [182]:
data_all.Text.loc[new_index] = sub_window_string
data_all.Text.loc[new_index]

67      GSK-3β is a major cyclin D1 kinase in lysates ...
231     E-cadherin is involved in the formation of cel...
233     E-cadherin is involved in the formation of cel...
235     E-cadherin is involved in the formation of cel...
450     The formation of protein complexes between pho...
461     The formation of protein complexes between pho...
505     The p16 gene is located in chromosome 9p21, a ...
543     4). Deletion or mutation of these CDK-inhibito...
547     4). Deletion or mutation of these CDK-inhibito...
548     4). Deletion or mutation of these CDK-inhibito...
664     In addition to its well-documented effects on ...
1226    HEREDITARY nonpolyposis colorectal cancer (HNP...
1997    However, cellular fluorescence evolves slowly ...
2363    Moreover, inactivation of the  placeholderGene...
2368    Moreover, inactivation of the  placeholderGene...
2370    Moreover, inactivation of the  placeholderGene...
2685    Hereditary nonpolyposis colon cancer (HN-PCC) ...
2814    4). De

# Extra investigation of test text

In [183]:
test_all = data_all.loc[len(new_train):]
all_text = list(test_all.Text)
test_all

Class       Gene   ID Variation  \
2925   NaN       WNT4    3     E216G   
2926   NaN     SUCLA2    4     G118R   
2927   NaN      CHEK2    6     E239K   
2928   NaN      CHST3    7     T141M   
2929   NaN       RNF6    8     G244D   
2930   NaN      SPAST    9     C448Y   
2931   NaN      SCN4A   11     V445M   
2932   NaN      ERBB2   15     G746S   
2933   NaN       TP53   16     Y234S   
2934   NaN     RAB27A   17      A87P   
2935   NaN       EGFR   18     P546S   
2936   NaN      ERBB2   19     G279E   
2937   NaN      CSF1R   20     Y969H   
2938   NaN     SLC7A9   22     V170M   
2939   NaN   ADAMTS13   23     A250V   
2940   NaN    DYNC2H1   25    Q1537R   
2941   NaN      TRPM1   27      L99P   
2942   NaN      SCN9A   28     N641Y   
2943   NaN     CYP7B1   30     F216S   
2944   NaN       SYT6   31     A406T   
2945   NaN      BCS1L   32     S277N   
2946   NaN      SCN9A   34     P149Q   
2947   NaN      SCN9A   35    I1461T   
2948   NaN       SCO1   36     P174L   
2949   NaN      CSF1R   38     Y969F   
2950   NaN       GJB3   39     E183K   
2951   NaN       TSHR   42     P162A   
2952   NaN      SMAD4   43     G386C   
2953   NaN    SLC17A5   46     P334R   
2954   NaN      ERBB2   47     V762M   
2955   NaN       GJB3   48      C86S   
2956   NaN        MET   50    M1268T   
2957   NaN      RPS26   51      D33N   
2958   NaN      RPS26   53       M1L   
2959   NaN       KRAS   54      Q61K   
2960   NaN       TSHR   55     R109Q   
2961   NaN   SLC25A15   56     R275Q   
2962   NaN      STK11   58     G163C   
2963   NaN      ABCC6   59    R1138Q   
2964   NaN      WISP3   61     S334P   
2965   NaN     PHOX2B   63     R100L   
2966   NaN       TSHR   66     C390W   
2967   NaN     PTPN11   67      A72D   
2968   NaN    B4GALT7   69     R270C   
2969   NaN    ALOX12B   70     H578Q   
2970   NaN       LRP4   71     D449N   
2971   NaN     PIK3CA   73     E545D   
2972   NaN       LRP4   76     D529N   
2973   NaN      SMAD4   78     D355E   
2974   NaN        GNE   80     R266W   
2975   NaN      SPAST   81      S44L   
2976   NaN        GNE   83     V572L   
2977   NaN      RBBP8   85     K337E   
2978   NaN     KISS1R   86     L148S   
2979   NaN        DCC   87    P1375H   
2980   NaN       CILP   90     I395T   
2981   NaN      KCNQ4   91     W276S   
2982   NaN    DYNC2H1   93    M1991L   
2983   NaN    SLC19A2   94      P51L   
2984   NaN       LRP6   96     R611C   
2985   NaN     SLC7A9   97     G259R   
2986   NaN       TSHR   98     M453T   
2987   NaN    SLC17A5  100     H183R   
2988   NaN      ABCC6  101    R1114P   
2989   NaN       TP53  103     R273S   
2990   NaN      ACVR1  104     R258M   
2991   NaN   SLC25A15  105      G27R   
2992   NaN     PIK3CA  106    G1049S   
2993   NaN   SLC25A15  107      L71Q   
2994   NaN       LRP5  108     R752G   
2995   NaN  TNFRSF11A  109      G53R   
2996   NaN      ABCC6  111    R1459C   
2997   NaN       ASS1  113     R108L   
2998   NaN       TSHR  116     P639S   
2999   NaN       TSHR  117     F631L   
3000   NaN     RAB27A  119     A152P   
3001   NaN      PRKRA  120     P222L   
3002   NaN       OTOF  124    P1825A   
3003   NaN       BBS5  125     T183A   
3004   NaN       CRB1  126     V162M   
3005   NaN      ABCC6  128    R1138W   
3006   NaN       IDH2  129     R140W   
3007   NaN     IKBKAP  130     R696P   
3008   NaN      SMAD4  132     G386S   
3009   NaN      SCN9A  133     L858H   
3010   NaN     CREBBP  134    R1446G   
3011   NaN     NDUFS3  135     R199W   
3012   NaN       MYOT  136      S60C   
3013   NaN     NDUFS6  137     C115Y   
3014   NaN      CSF1R  138     Y571D   
3015   NaN      SCN9A  140    V1299F   
3016   NaN      DNAI1  142     G515S   
3017   NaN        GNE  143     G607E   
3018   NaN      STK11  144      R86G   
3019   NaN     PLA2G6  145      A80T   
3020   NaN      SCN4A  148    V1293I   
3021   NaN       EDAR  149     R375H   
3022   NaN      SEPT9  150      R88W   
3023   NaN       WNT4  151     A114V   
3024 

In [184]:
positions_machine = []
all_together = []
for i in range(len(all_text)):
    text = all_text[i]
    if text.count('placeholderMutation') < 11:
        all_together.append((i, text.count('placeholderMutation')))
        positions_machine.append(i)

In [185]:
important_texts = [all_text[i] for i in positions_machine]
test_all.iloc[positions_machine]

Class    Gene   ID Variation  \
2929   NaN    RNF6    8     G244D   
2932   NaN   ERBB2   15     G746S   
2933   NaN    TP53   16     Y234S   
2937   NaN   CSF1R   20     Y969H   
2944   NaN    SYT6   31     A406T   
2949   NaN   CSF1R   38     Y969F   
2952   NaN   SMAD4   43     G386C   
2954   NaN   ERBB2   47     V762M   
2956   NaN     MET   50    M1268T   
2959   NaN    KRAS   54      Q61K   
2962   NaN   STK11   58     G163C   
2971   NaN  PIK3CA   73     E545D   
2973   NaN   SMAD4   78     D355E   
2979   NaN     DCC   87    P1375H   
2990   NaN   ACVR1  104     R258M   
2992   NaN  PIK3CA  106    G1049S   
3008   NaN   SMAD4  132     G386S   
3010   NaN  CREBBP  134    R1446G   
3018   NaN   STK11  144      R86G   
3026   NaN    AKT2  156     S302G   
3030   NaN     MYC  161      P58L   
3033   NaN    TP53  165     S241A   
3045   NaN   ERBB2  187     D739Y   
3048   NaN    EGFR  190     K745R   
3050   NaN  MAP2K1  195      F53V   
3053   NaN   SF3B2  201     E700G   
3068   NaN    XPO1  224     E571V   
3072   NaN  MAP2K1  228      F53I   
3073   NaN    TP53  229     R282P   
3085   NaN  CTNNB1  251      S37P   
3089   NaN    TP53  255     R249T   
3091   NaN   CSF1R  258     L301S   
3104   NaN    TP53  278     V173G   
3107   NaN  PIK3CA  281    T1025A   
3113   NaN    KRAS  289      G13S   
3135   NaN  CTNNB1  326      T40A   
3150   NaN     MCC  350     A888V   
3159   NaN  CTNNB1  365      D32V   
3177   NaN   FGFR2  396     N639K   
3180   NaN    PTEN  403     R159S   
3189   NaN    GJB3  419      L34P   
3191   NaN   ERBB2  422     L755M   
3192   NaN     MCC  423     R696Q   
3195   NaN    ASS1  426      S18L   
3197   NaN   EPHA5  431     G583E   
3198   NaN    KRAS  433     A146P   
3207   NaN    EGFR  443     E749Q   
3210   NaN   STK11  447     Q123R   
3211   NaN  CDKN2A  448     A128D   
3216   NaN    NRAS  454      G13R   
3219   NaN    EGFR  459     E734K   
3220   NaN   ERBB2  463     N827S   
3221   NaN  PIK3CA  464     Q546L   
3222   NaN  CRNKL1  465     S116F   
3225   NaN  CTNNB1  469      T41I   
3227   NaN    TP53  471     R148I   
3229   NaN    NRAS  476      G13S   
3231   NaN  NOTCH1  480    D1642H   
3234   NaN   FGFR3  485     E322K   
3249   NaN   STK11  508     D194E   
3251   NaN    IDH2  510     R120M   
3254   NaN  NOTCH1  515    R2327W   
3257   NaN    TP53  518      S83I   
3258   NaN  CDKN2A  519      A97V   
3261   NaN  CTNNB1  522      D32H   
3269   NaN    TP53  536     Y234N   
3271   NaN    NEK8  538     A197P   
3275   NaN   CSF1R  546     Y969C   
3277   NaN     VHL  550      L89H   
3285   NaN   CSF1R  567     L301F   
3298   NaN    TP53  591     V173A   
3300   NaN   SMAD4  593     R361P   
3303   NaN  CDKN2A  601      A97G   
3304   NaN    EGFR  602     A289T   
3318   NaN   SMAD4  626     G386V   
3320   NaN    TP53  628     T125P   
3321   NaN  CTNNB1  632      T41N   
3327   NaN   FGFR2  643     C383Y   
3334   NaN     MYC  660      T73P   
3340   NaN    XPO1  668     E571A   
3345   NaN     TTK  676     D697Y   
3357   NaN   XRCC1  692     R194W   
3369   NaN  CTNNB1  710      G34R   
3371   NaN    BRAF  713     D594H   
3374   NaN     DCC  720     M168T   
3375   NaN   STK11  721     S216F   
3379   NaN  CTNNB1  727      S45C   
3380   NaN   SMAD4  730     G386A   
3384   NaN    BRAF  737     N581T   
3390   NaN   SMAD4  747     R361S   
3404   NaN    EGFR  769     E746K   
3405   NaN   SMAD4  770     R361H   
3408   NaN    TP53  776     Y220D   
3411   NaN    KRAS  780      G13A   
3416   NaN    TP53  789     R213L   
3423   NaN   STK19  797      D89N   
3424   NaN    EGFR  798     R108G   
3425   NaN    EGFR  800     S752Y   
3426   NaN   MED12  801    L1224V   
3434   NaN   FGFR2  816     Y382H   
3436   NaN     MET  819    H1112Y   
3438   NaN   SMAD4  824     R361G   
3443   NaN   ERBB2  832     S280Y   
3450   NaN    EGFR  845     G598A   
3451   NaN    KRAS  846      Q61E   
3453   NaN   STK33  852     F136L   
3454   NaN   FGFR2  853     S320C   
3459   Na

In [186]:
all_together

[(4, 2),
 (7, 2),
 (8, 0),
 (12, 0),
 (19, 0),
 (24, 0),
 (27, 2),
 (29, 1),
 (31, 7),
 (34, 1),
 (37, 0),
 (46, 3),
 (48, 2),
 (54, 0),
 (65, 0),
 (67, 3),
 (83, 1),
 (85, 5),
 (93, 0),
 (101, 0),
 (105, 0),
 (108, 0),
 (120, 7),
 (123, 5),
 (125, 3),
 (128, 0),
 (143, 0),
 (147, 3),
 (148, 0),
 (160, 0),
 (164, 0),
 (166, 0),
 (179, 3),
 (182, 0),
 (188, 2),
 (210, 0),
 (225, 0),
 (234, 2),
 (252, 0),
 (255, 0),
 (264, 8),
 (266, 0),
 (267, 0),
 (270, 0),
 (272, 1),
 (273, 0),
 (282, 0),
 (285, 0),
 (286, 3),
 (291, 2),
 (294, 4),
 (295, 0),
 (296, 1),
 (297, 1),
 (300, 1),
 (302, 0),
 (304, 2),
 (306, 0),
 (309, 4),
 (324, 3),
 (326, 1),
 (329, 0),
 (332, 0),
 (333, 7),
 (336, 5),
 (344, 0),
 (346, 1),
 (350, 0),
 (352, 2),
 (360, 0),
 (373, 0),
 (375, 0),
 (378, 0),
 (379, 1),
 (393, 5),
 (395, 0),
 (396, 1),
 (402, 0),
 (409, 0),
 (415, 0),
 (420, 1),
 (432, 2),
 (444, 1),
 (446, 3),
 (449, 0),
 (450, 0),
 (454, 3),
 (455, 5),
 (459, 2),
 (465, 5),
 (479, 2),
 (480, 0),
 (483, 0),

In [187]:
test_important = test_all.iloc[positions_machine]
test_important

Class    Gene   ID Variation  \
2929   NaN    RNF6    8     G244D   
2932   NaN   ERBB2   15     G746S   
2933   NaN    TP53   16     Y234S   
2937   NaN   CSF1R   20     Y969H   
2944   NaN    SYT6   31     A406T   
2949   NaN   CSF1R   38     Y969F   
2952   NaN   SMAD4   43     G386C   
2954   NaN   ERBB2   47     V762M   
2956   NaN     MET   50    M1268T   
2959   NaN    KRAS   54      Q61K   
2962   NaN   STK11   58     G163C   
2971   NaN  PIK3CA   73     E545D   
2973   NaN   SMAD4   78     D355E   
2979   NaN     DCC   87    P1375H   
2990   NaN   ACVR1  104     R258M   
2992   NaN  PIK3CA  106    G1049S   
3008   NaN   SMAD4  132     G386S   
3010   NaN  CREBBP  134    R1446G   
3018   NaN   STK11  144      R86G   
3026   NaN    AKT2  156     S302G   
3030   NaN     MYC  161      P58L   
3033   NaN    TP53  165     S241A   
3045   NaN   ERBB2  187     D739Y   
3048   NaN    EGFR  190     K745R   
3050   NaN  MAP2K1  195      F53V   
3053   NaN   SF3B2  201     E700G   
3068   NaN    XPO1  224     E571V   
3072   NaN  MAP2K1  228      F53I   
3073   NaN    TP53  229     R282P   
3085   NaN  CTNNB1  251      S37P   
3089   NaN    TP53  255     R249T   
3091   NaN   CSF1R  258     L301S   
3104   NaN    TP53  278     V173G   
3107   NaN  PIK3CA  281    T1025A   
3113   NaN    KRAS  289      G13S   
3135   NaN  CTNNB1  326      T40A   
3150   NaN     MCC  350     A888V   
3159   NaN  CTNNB1  365      D32V   
3177   NaN   FGFR2  396     N639K   
3180   NaN    PTEN  403     R159S   
3189   NaN    GJB3  419      L34P   
3191   NaN   ERBB2  422     L755M   
3192   NaN     MCC  423     R696Q   
3195   NaN    ASS1  426      S18L   
3197   NaN   EPHA5  431     G583E   
3198   NaN    KRAS  433     A146P   
3207   NaN    EGFR  443     E749Q   
3210   NaN   STK11  447     Q123R   
3211   NaN  CDKN2A  448     A128D   
3216   NaN    NRAS  454      G13R   
3219   NaN    EGFR  459     E734K   
3220   NaN   ERBB2  463     N827S   
3221   NaN  PIK3CA  464     Q546L   
3222   NaN  CRNKL1  465     S116F   
3225   NaN  CTNNB1  469      T41I   
3227   NaN    TP53  471     R148I   
3229   NaN    NRAS  476      G13S   
3231   NaN  NOTCH1  480    D1642H   
3234   NaN   FGFR3  485     E322K   
3249   NaN   STK11  508     D194E   
3251   NaN    IDH2  510     R120M   
3254   NaN  NOTCH1  515    R2327W   
3257   NaN    TP53  518      S83I   
3258   NaN  CDKN2A  519      A97V   
3261   NaN  CTNNB1  522      D32H   
3269   NaN    TP53  536     Y234N   
3271   NaN    NEK8  538     A197P   
3275   NaN   CSF1R  546     Y969C   
3277   NaN     VHL  550      L89H   
3285   NaN   CSF1R  567     L301F   
3298   NaN    TP53  591     V173A   
3300   NaN   SMAD4  593     R361P   
3303   NaN  CDKN2A  601      A97G   
3304   NaN    EGFR  602     A289T   
3318   NaN   SMAD4  626     G386V   
3320   NaN    TP53  628     T125P   
3321   NaN  CTNNB1  632      T41N   
3327   NaN   FGFR2  643     C383Y   
3334   NaN     MYC  660      T73P   
3340   NaN    XPO1  668     E571A   
3345   NaN     TTK  676     D697Y   
3357   NaN   XRCC1  692     R194W   
3369   NaN  CTNNB1  710      G34R   
3371   NaN    BRAF  713     D594H   
3374   NaN     DCC  720     M168T   
3375   NaN   STK11  721     S216F   
3379   NaN  CTNNB1  727      S45C   
3380   NaN   SMAD4  730     G386A   
3384   NaN    BRAF  737     N581T   
3390   NaN   SMAD4  747     R361S   
3404   NaN    EGFR  769     E746K   
3405   NaN   SMAD4  770     R361H   
3408   NaN    TP53  776     Y220D   
3411   NaN    KRAS  780      G13A   
3416   NaN    TP53  789     R213L   
3423   NaN   STK19  797      D89N   
3424   NaN    EGFR  798     R108G   
3425   NaN    EGFR  800     S752Y   
3426   NaN   MED12  801    L1224V   
3434   NaN   FGFR2  816     Y382H   
3436   NaN     MET  819    H1112Y   
3438   NaN   SMAD4  824     R361G   
3443   NaN   ERBB2  832     S280Y   
3450   NaN    EGFR  845     G598A   
3451   NaN    KRAS  846      Q61E   
3453   NaN   STK33  852     F136L   
3454   NaN   FGFR2  853     S320C   
3459   Na

In [188]:
test_important.Text[test_important.index[20]]

'Among the best-studied therapeutic targets in human cancers are proteins encoded by genes with tumor-specific mutational hotspots, such as KRAS, NRAS, BRAF, KIT, and EGFR. The acquisition of somatic mutations is one of the major mechanisms responsible for the dysregulation of proliferation, invasion, and apoptosis that is required for oncogenesis. These computational approaches develop either gene-level statistical models that exploit different mutational patterns3–6 to identify significantly mutated genes or use weight-of-evidence-based methods1,7 that are heuristic and ratiometric in approach. However, emerging data indicate that different hotspot mutations in the same cancer gene can be functionally distinct in vitro and in vivo and display different clinical phenotypes and drug sensitivity8–11. To date, studies of hotspot mutations in cancer have been limited to within individual tumor types12–14 or have focused on individual cancer genes across tumor types15. A systematic populat

# Adding gene dummy and Full_text

In [189]:
shared_genes = list(set(train_all.Gene).intersection(set(test_all.Gene))) # the shared genes are those that appear in both
count_important = 0
for gene in test_important.Gene:
    if gene in shared_genes:
        count_important += 1

count_important # so 104 EXAMPLES in test where same gene appears as in the impo

104

In [190]:
len(shared_genes)

35

In [191]:
shared_genes

['PTEN',
 'XPO1',
 'IDH1',
 'BCL10',
 'TP53',
 'VHL',
 'MED12',
 'DNMT3A',
 'RAD50',
 'EGFR',
 'MET',
 'CHEK2',
 'CREBBP',
 'AKT2',
 'RAD54L',
 'FGFR2',
 'ERBB2',
 'PIK3CA',
 'CDKN2A',
 'BRAF',
 'MAP2K1',
 'RAC1',
 'ACVR1',
 'NRAS',
 'FGFR3',
 'STK11',
 'KRAS',
 'IDH2',
 'MYC',
 'NOTCH1',
 'CDK4',
 'PTPN11',
 'EPAS1',
 'CTNNB1',
 'SMAD4']

In [192]:
for gene in shared_genes:
    data_all[gene] = 0
data_all

Class       Gene   ID Variation  \
0        2        CBL    1     W802*   
1        2        CBL    2     Q249E   
2        3        CBL    3     N454D   
3        4        CBL    4     L399V   
4        4        CBL    5     V391I   
5        5        CBL    6     V430M   
6        4        CBL    8     Y371H   
7        4        CBL    9     C384R   
8        4        CBL   10     P395A   
9        4        CBL   11     K382E   
10       4        CBL   12     R420Q   
11       4        CBL   13     C381A   
12       5        CBL   14     P428L   
13       4        CBL   15     D390Y   
14       4        CBL   17     Q367P   
15       5        CBL   18     M374V   
16       4        CBL   19     Y371S   
17       6        CBL   20      H94Y   
18       4        CBL   21     C396R   
19       4        CBL   22     G375P   
20       4        CBL   23     S376F   
21       4        CBL   24     P417A   
22       4        CBL   25     H398Y   
23       4      SHOC2   26       S2G   
24       4       TERT   27     Y846C   
25       7       TERT   28     C228T   
26       4       TERT   29     H412Y   
27       4       TERT   30     H876Q   
28       4       TERT   32     P704S   
29       7       TERT   34     C250T   
30       4     DICER1   35    G1809R   
31       4     DICER1   36    G1809K   
32       1     DICER1   37    D1709E   
33       1     DICER1   38    D1709A   
34       4     DICER1   39    E1705A   
35       4     DICER1   40    D1810A   
36       4     DICER1   42    E1705K   
37       4      PTPRT   44    T1365M   
38       1      PTPRT   45     V648G   
39       4      PTPRT   46     T844M   
40       1      PTPRT   47     A707T   
41       4      PTPRT   49    R1343L   
42       1      PTPRT   50     A209T   
43       1      PTPRT   51     Y280H   
44       4      PTPRT   52     D927G   
45       1      PTPRT   53     N510K   
46       1      PTPRT   54     F248S   
47       1      PTPRT   55     L708P   
48       4      PTPRT   56     V995M   
49       1      PTPRT   57     Y412F   
50       1      PTPRT   58      F74S   
51       1      PTPRT   59    R1040L   
52       1      PTPRT   60     R453C   
53       4      PTPRT   61    R1209W   
54       4      PTPRT   62    A1022E   
55       4      PTPRT   63     Q984K   
56       1      PTPRT   64     T605M   
57       1      PTPRT   65     K218T   
58       4      PTPRT   66    N1125I   
59       7       RHEB   67      Y35C   
60       7       RHEB   68      Y35N   
61       7       RHEB   69      Y35H   
62       4      RAD50   73    L1273F   
63       2      CCND3   76     P284L   
64       7      CCND3   77     Q276*   
65       7      CCND3   78     T286A   
66       7      CCND3   79     T283A   
67       2      CCND3   80     I290A   
68       2      CCND3   81     I290R   
69       7       RIT1   82      A77S   
70       7       RIT1   83      A77P   
71       2       RIT1   84      A77T   
72       7       RIT1   85      M90I   
73       4     TGFBR1   89      N45S   
74       1     TGFBR1   90     R487Q   
75       4     TGFBR1   91      C41Y   
76       4     TGFBR1   92      G52R   
77       4     TGFBR1   93      P83L   
78       1     TGFBR1   94     S241L   
79       4     TGFBR1   95     S387Y   
80       2     TGFBR2   97     R537P   
81       4     TGFBR2   98     D404G   
82       4     TGFBR2   99     P525L   
83       4       MSH6  102     R922*   
84       1       MSH6  103     R976H   
85       4       MSH6  104    E1322*   
86       1       MSH6  105    T1219I   
87       5       MSH6  106      G39E   
88       1       MSH6  108    R1076C   
89       5       MSH6  109    R1095H   
90       5       MSH6  111     V509A   
91       4       MSH6  112     E946*   
92       8      SF3B1  121     K700R   
93       9      SF3B1  122     R625C   
94       9      SF3B1  123     E622D   
95       9      SF3B1  124     H662Q   
96       9      SF3B1  125     R625D   
97       9      SF3B1  126     K666M   
98       9      SF3B1  127     H662R   
99   

In [193]:
for i in data_all.index:
    gene = data_all.Gene[i]
    if gene in shared_genes:
        data_all.loc[i, gene] = 1

data_all # it's not all zeros, it looks like it but genes like BRAF and EFGR have more 1's because they occur more

Class       Gene   ID Variation  \
0        2        CBL    1     W802*   
1        2        CBL    2     Q249E   
2        3        CBL    3     N454D   
3        4        CBL    4     L399V   
4        4        CBL    5     V391I   
5        5        CBL    6     V430M   
6        4        CBL    8     Y371H   
7        4        CBL    9     C384R   
8        4        CBL   10     P395A   
9        4        CBL   11     K382E   
10       4        CBL   12     R420Q   
11       4        CBL   13     C381A   
12       5        CBL   14     P428L   
13       4        CBL   15     D390Y   
14       4        CBL   17     Q367P   
15       5        CBL   18     M374V   
16       4        CBL   19     Y371S   
17       6        CBL   20      H94Y   
18       4        CBL   21     C396R   
19       4        CBL   22     G375P   
20       4        CBL   23     S376F   
21       4        CBL   24     P417A   
22       4        CBL   25     H398Y   
23       4      SHOC2   26       S2G   
24       4       TERT   27     Y846C   
25       7       TERT   28     C228T   
26       4       TERT   29     H412Y   
27       4       TERT   30     H876Q   
28       4       TERT   32     P704S   
29       7       TERT   34     C250T   
30       4     DICER1   35    G1809R   
31       4     DICER1   36    G1809K   
32       1     DICER1   37    D1709E   
33       1     DICER1   38    D1709A   
34       4     DICER1   39    E1705A   
35       4     DICER1   40    D1810A   
36       4     DICER1   42    E1705K   
37       4      PTPRT   44    T1365M   
38       1      PTPRT   45     V648G   
39       4      PTPRT   46     T844M   
40       1      PTPRT   47     A707T   
41       4      PTPRT   49    R1343L   
42       1      PTPRT   50     A209T   
43       1      PTPRT   51     Y280H   
44       4      PTPRT   52     D927G   
45       1      PTPRT   53     N510K   
46       1      PTPRT   54     F248S   
47       1      PTPRT   55     L708P   
48       4      PTPRT   56     V995M   
49       1      PTPRT   57     Y412F   
50       1      PTPRT   58      F74S   
51       1      PTPRT   59    R1040L   
52       1      PTPRT   60     R453C   
53       4      PTPRT   61    R1209W   
54       4      PTPRT   62    A1022E   
55       4      PTPRT   63     Q984K   
56       1      PTPRT   64     T605M   
57       1      PTPRT   65     K218T   
58       4      PTPRT   66    N1125I   
59       7       RHEB   67      Y35C   
60       7       RHEB   68      Y35N   
61       7       RHEB   69      Y35H   
62       4      RAD50   73    L1273F   
63       2      CCND3   76     P284L   
64       7      CCND3   77     Q276*   
65       7      CCND3   78     T286A   
66       7      CCND3   79     T283A   
67       2      CCND3   80     I290A   
68       2      CCND3   81     I290R   
69       7       RIT1   82      A77S   
70       7       RIT1   83      A77P   
71       2       RIT1   84      A77T   
72       7       RIT1   85      M90I   
73       4     TGFBR1   89      N45S   
74       1     TGFBR1   90     R487Q   
75       4     TGFBR1   91      C41Y   
76       4     TGFBR1   92      G52R   
77       4     TGFBR1   93      P83L   
78       1     TGFBR1   94     S241L   
79       4     TGFBR1   95     S387Y   
80       2     TGFBR2   97     R537P   
81       4     TGFBR2   98     D404G   
82       4     TGFBR2   99     P525L   
83       4       MSH6  102     R922*   
84       1       MSH6  103     R976H   
85       4       MSH6  104    E1322*   
86       1       MSH6  105    T1219I   
87       5       MSH6  106      G39E   
88       1       MSH6  108    R1076C   
89       5       MSH6  109    R1095H   
90       5       MSH6  111     V509A   
91       4       MSH6  112     E946*   
92       8      SF3B1  121     K700R   
93       9      SF3B1  122     R625C   
94       9      SF3B1  123     E622D   
95       9      SF3B1  124     H662Q   
96       9      SF3B1  125     R625D   
97       9      SF3B1  126     K666M   
98       9      SF3B1  127     H662R   
99   

In [194]:
# We decided to go for 15 dummies for genes:
N_components = 15
svd = TruncatedSVD(n_components= N_components, n_iter=18, random_state=18)
data_text = data_all[['Class', 'Gene', 'ID', 'Variation','Text']] #5th is Text, just before the genes 
one_hot_gene = data_all[shared_genes]

truncated_one_hot_gene = svd.fit_transform(one_hot_gene.values)
print(svd.explained_variance_ratio_.sum())

0.846437054329


In [195]:
genes_df =pd.DataFrame(truncated_one_hot_gene,columns=["tsvd_gene"+ str(x) for x in range(N_components)])
genes_df

tsvd_gene0    tsvd_gene1    tsvd_gene2    tsvd_gene3    tsvd_gene4  \
0    -4.687577e-24 -6.120573e-20 -2.015694e-20 -2.202339e-22  1.757299e-22   
1     6.531017e-22 -1.105960e-18  7.176205e-17  6.392266e-19 -4.231921e-19   
2    -1.936228e-24  1.235412e-21 -9.429628e-20  1.236044e-17 -2.559256e-17   
3    -1.936252e-25  5.014914e-20  1.336022e-18 -3.148571e-15 -4.521623e-15   
4    -5.494071e-26  9.687730e-23 -8.270054e-22 -2.321849e-19  1.723147e-18   
5     7.952901e-26 -1.557783e-22  4.261542e-21  1.230154e-18  9.799194e-19   
6     2.322664e-27  1.012991e-24  4.924734e-23  1.256177e-20  5.618518e-20   
7     5.928725e-27 -8.832844e-25  6.759233e-23  4.656283e-20  2.369380e-20   
8     4.148274e-27 -3.627361e-24  3.518046e-23  7.118104e-22 -2.898922e-20   
9    -8.596720e-27  1.582616e-24 -1.525188e-22 -1.716718e-21 -1.965893e-19   
10   -6.008866e-27  1.183450e-24 -1.057986e-22 -6.094275e-21 -1.469852e-19   
11   -2.714005e-28  4.980867e-26 -4.717511e-24 -2.504300e-22 -6.664642e-21   
12   -1.200460e-28  1.358050e-26 -1.954409e-24 -4.806801e-23 -2.990105e-21   
13    3.009091e-32 -2.068437e-29  7.067966e-28  8.117756e-26 -1.272528e-25   
14   -7.484862e-31  5.833903e-28 -1.779281e-26 -5.556587e-25 -1.879963e-24   
15   -4.394591e-30  1.936807e-27 -1.372109e-25  8.644772e-24 -9.295606e-23   
16   -1.397102e-36 -4.381137e-34  7.317601e-33 -1.396895e-29 -4.082990e-31   
17    9.999252e-35 -6.228332e-32  5.611649e-30 -1.282023e-27  4.347328e-27   
18   -9.678765e-38 -8.247264e-35 -5.215052e-33  1.196047e-31 -2.649260e-30   
19    4.540499e-38  1.634124e-35  1.977758e-33 -7.374660e-32  1.218743e-30   
20    2.837386e-41 -4.542488e-39  2.564937e-37  7.817461e-35 -1.030015e-35   
21    1.798685e-40 -2.301990e-37 -1.184308e-36  3.865188e-34 -2.905607e-33   
22   -6.142949e-41 -2.488329e-38 -2.256609e-38 -2.045409e-34 -2.814576e-34   
23   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
24   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
25   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
26   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
27   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
28   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
29   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
30   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
31   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
32   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
33   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
34   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
35   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
36   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
37   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
38   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
39   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
40   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
41   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
42   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
43   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
44   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
45   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
46   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
47   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
48   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
49   -0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
50   -0.000000e+00  0.000000e+

In [208]:
data_final = pd.merge(data_text.reset_index(), genes_df.reset_index()).drop("index",axis=1)

In [209]:
data_final

Class       Gene   ID Variation  \
0        2        CBL    1     W802*   
1        2        CBL    2     Q249E   
2        3        CBL    3     N454D   
3        4        CBL    4     L399V   
4        4        CBL    5     V391I   
5        5        CBL    6     V430M   
6        4        CBL    8     Y371H   
7        4        CBL    9     C384R   
8        4        CBL   10     P395A   
9        4        CBL   11     K382E   
10       4        CBL   12     R420Q   
11       4        CBL   13     C381A   
12       5        CBL   14     P428L   
13       4        CBL   15     D390Y   
14       4        CBL   17     Q367P   
15       5        CBL   18     M374V   
16       4        CBL   19     Y371S   
17       6        CBL   20      H94Y   
18       4        CBL   21     C396R   
19       4        CBL   22     G375P   
20       4        CBL   23     S376F   
21       4        CBL   24     P417A   
22       4        CBL   25     H398Y   
23       4      SHOC2   26       S2G   
24       4       TERT   27     Y846C   
25       7       TERT   28     C228T   
26       4       TERT   29     H412Y   
27       4       TERT   30     H876Q   
28       4       TERT   32     P704S   
29       7       TERT   34     C250T   
30       4     DICER1   35    G1809R   
31       4     DICER1   36    G1809K   
32       1     DICER1   37    D1709E   
33       1     DICER1   38    D1709A   
34       4     DICER1   39    E1705A   
35       4     DICER1   40    D1810A   
36       4     DICER1   42    E1705K   
37       4      PTPRT   44    T1365M   
38       1      PTPRT   45     V648G   
39       4      PTPRT   46     T844M   
40       1      PTPRT   47     A707T   
41       4      PTPRT   49    R1343L   
42       1      PTPRT   50     A209T   
43       1      PTPRT   51     Y280H   
44       4      PTPRT   52     D927G   
45       1      PTPRT   53     N510K   
46       1      PTPRT   54     F248S   
47       1      PTPRT   55     L708P   
48       4      PTPRT   56     V995M   
49       1      PTPRT   57     Y412F   
50       1      PTPRT   58      F74S   
51       1      PTPRT   59    R1040L   
52       1      PTPRT   60     R453C   
53       4      PTPRT   61    R1209W   
54       4      PTPRT   62    A1022E   
55       4      PTPRT   63     Q984K   
56       1      PTPRT   64     T605M   
57       1      PTPRT   65     K218T   
58       4      PTPRT   66    N1125I   
59       7       RHEB   67      Y35C   
60       7       RHEB   68      Y35N   
61       7       RHEB   69      Y35H   
62       4      RAD50   73    L1273F   
63       2      CCND3   76     P284L   
64       7      CCND3   77     Q276*   
65       7      CCND3   78     T286A   
66       7      CCND3   79     T283A   
67       2      CCND3   80     I290A   
68       2      CCND3   81     I290R   
69       7       RIT1   82      A77S   
70       7       RIT1   83      A77P   
71       2       RIT1   84      A77T   
72       7       RIT1   85      M90I   
73       4     TGFBR1   89      N45S   
74       1     TGFBR1   90     R487Q   
75       4     TGFBR1   91      C41Y   
76       4     TGFBR1   92      G52R   
77       4     TGFBR1   93      P83L   
78       1     TGFBR1   94     S241L   
79       4     TGFBR1   95     S387Y   
80       2     TGFBR2   97     R537P   
81       4     TGFBR2   98     D404G   
82       4     TGFBR2   99     P525L   
83       4       MSH6  102     R922*   
84       1       MSH6  103     R976H   
85       4       MSH6  104    E1322*   
86       1       MSH6  105    T1219I   
87       5       MSH6  106      G39E   
88       1       MSH6  108    R1076C   
89       5       MSH6  109    R1095H   
90       5       MSH6  111     V509A   
91       4       MSH6  112     E946*   
92       8      SF3B1  121     K700R   
93       9      SF3B1  122     R625C   
94       9      SF3B1  123     E622D   
95       9      SF3B1  124     H662Q   
96       9      SF3B1  125     R625D   
97       9      SF3B1  126     K666M   
98       9      SF3B1  127     H662R   
99   

In [210]:
# Replace column name for text of window, and add new column of full text
data_final.insert(loc=4, column='Full_Text', value=data_all_backup.Text)
data_final.columns.values[5] = 'Window_Text'
data_final

Class       Gene   ID Variation  \
0        2        CBL    1     W802*   
1        2        CBL    2     Q249E   
2        3        CBL    3     N454D   
3        4        CBL    4     L399V   
4        4        CBL    5     V391I   
5        5        CBL    6     V430M   
6        4        CBL    8     Y371H   
7        4        CBL    9     C384R   
8        4        CBL   10     P395A   
9        4        CBL   11     K382E   
10       4        CBL   12     R420Q   
11       4        CBL   13     C381A   
12       5        CBL   14     P428L   
13       4        CBL   15     D390Y   
14       4        CBL   17     Q367P   
15       5        CBL   18     M374V   
16       4        CBL   19     Y371S   
17       6        CBL   20      H94Y   
18       4        CBL   21     C396R   
19       4        CBL   22     G375P   
20       4        CBL   23     S376F   
21       4        CBL   24     P417A   
22       4        CBL   25     H398Y   
23       4      SHOC2   26       S2G   
24       4       TERT   27     Y846C   
25       7       TERT   28     C228T   
26       4       TERT   29     H412Y   
27       4       TERT   30     H876Q   
28       4       TERT   32     P704S   
29       7       TERT   34     C250T   
30       4     DICER1   35    G1809R   
31       4     DICER1   36    G1809K   
32       1     DICER1   37    D1709E   
33       1     DICER1   38    D1709A   
34       4     DICER1   39    E1705A   
35       4     DICER1   40    D1810A   
36       4     DICER1   42    E1705K   
37       4      PTPRT   44    T1365M   
38       1      PTPRT   45     V648G   
39       4      PTPRT   46     T844M   
40       1      PTPRT   47     A707T   
41       4      PTPRT   49    R1343L   
42       1      PTPRT   50     A209T   
43       1      PTPRT   51     Y280H   
44       4      PTPRT   52     D927G   
45       1      PTPRT   53     N510K   
46       1      PTPRT   54     F248S   
47       1      PTPRT   55     L708P   
48       4      PTPRT   56     V995M   
49       1      PTPRT   57     Y412F   
50       1      PTPRT   58      F74S   
51       1      PTPRT   59    R1040L   
52       1      PTPRT   60     R453C   
53       4      PTPRT   61    R1209W   
54       4      PTPRT   62    A1022E   
55       4      PTPRT   63     Q984K   
56       1      PTPRT   64     T605M   
57       1      PTPRT   65     K218T   
58       4      PTPRT   66    N1125I   
59       7       RHEB   67      Y35C   
60       7       RHEB   68      Y35N   
61       7       RHEB   69      Y35H   
62       4      RAD50   73    L1273F   
63       2      CCND3   76     P284L   
64       7      CCND3   77     Q276*   
65       7      CCND3   78     T286A   
66       7      CCND3   79     T283A   
67       2      CCND3   80     I290A   
68       2      CCND3   81     I290R   
69       7       RIT1   82      A77S   
70       7       RIT1   83      A77P   
71       2       RIT1   84      A77T   
72       7       RIT1   85      M90I   
73       4     TGFBR1   89      N45S   
74       1     TGFBR1   90     R487Q   
75       4     TGFBR1   91      C41Y   
76       4     TGFBR1   92      G52R   
77       4     TGFBR1   93      P83L   
78       1     TGFBR1   94     S241L   
79       4     TGFBR1   95     S387Y   
80       2     TGFBR2   97     R537P   
81       4     TGFBR2   98     D404G   
82       4     TGFBR2   99     P525L   
83       4       MSH6  102     R922*   
84       1       MSH6  103     R976H   
85       4       MSH6  104    E1322*   
86       1       MSH6  105    T1219I   
87       5       MSH6  106      G39E   
88       1       MSH6  108    R1076C   
89       5       MSH6  109    R1095H   
90       5       MSH6  111     V509A   
91       4       MSH6  112     E946*   
92       8      SF3B1  121     K700R   
93       9      SF3B1  122     R625C   
94       9      SF3B1  123     E622D   
95       9      SF3B1  124     H662Q   
96       9      SF3B1  125     R625D   
97       9      SF3B1  126     K666M   
98       9      SF3B1  127     H662R   
99   

In [551]:
new_train_1 = data_final.iloc[:len(new_train)]
new_test_1 = data_final.iloc[len(new_train):]

In [553]:
new_test_1

Class       Gene   ID Variation  \
2925   NaN       WNT4    3     E216G   
2926   NaN     SUCLA2    4     G118R   
2927   NaN      CHEK2    6     E239K   
2928   NaN      CHST3    7     T141M   
2929   NaN       RNF6    8     G244D   
2930   NaN      SPAST    9     C448Y   
2931   NaN      SCN4A   11     V445M   
2932   NaN      ERBB2   15     G746S   
2933   NaN       TP53   16     Y234S   
2934   NaN     RAB27A   17      A87P   
2935   NaN       EGFR   18     P546S   
2936   NaN      ERBB2   19     G279E   
2937   NaN      CSF1R   20     Y969H   
2938   NaN     SLC7A9   22     V170M   
2939   NaN   ADAMTS13   23     A250V   
2940   NaN    DYNC2H1   25    Q1537R   
2941   NaN      TRPM1   27      L99P   
2942   NaN      SCN9A   28     N641Y   
2943   NaN     CYP7B1   30     F216S   
2944   NaN       SYT6   31     A406T   
2945   NaN      BCS1L   32     S277N   
2946   NaN      SCN9A   34     P149Q   
2947   NaN      SCN9A   35    I1461T   
2948   NaN       SCO1   36     P174L   
2949   NaN      CSF1R   38     Y969F   
2950   NaN       GJB3   39     E183K   
2951   NaN       TSHR   42     P162A   
2952   NaN      SMAD4   43     G386C   
2953   NaN    SLC17A5   46     P334R   
2954   NaN      ERBB2   47     V762M   
2955   NaN       GJB3   48      C86S   
2956   NaN        MET   50    M1268T   
2957   NaN      RPS26   51      D33N   
2958   NaN      RPS26   53       M1L   
2959   NaN       KRAS   54      Q61K   
2960   NaN       TSHR   55     R109Q   
2961   NaN   SLC25A15   56     R275Q   
2962   NaN      STK11   58     G163C   
2963   NaN      ABCC6   59    R1138Q   
2964   NaN      WISP3   61     S334P   
2965   NaN     PHOX2B   63     R100L   
2966   NaN       TSHR   66     C390W   
2967   NaN     PTPN11   67      A72D   
2968   NaN    B4GALT7   69     R270C   
2969   NaN    ALOX12B   70     H578Q   
2970   NaN       LRP4   71     D449N   
2971   NaN     PIK3CA   73     E545D   
2972   NaN       LRP4   76     D529N   
2973   NaN      SMAD4   78     D355E   
2974   NaN        GNE   80     R266W   
2975   NaN      SPAST   81      S44L   
2976   NaN        GNE   83     V572L   
2977   NaN      RBBP8   85     K337E   
2978   NaN     KISS1R   86     L148S   
2979   NaN        DCC   87    P1375H   
2980   NaN       CILP   90     I395T   
2981   NaN      KCNQ4   91     W276S   
2982   NaN    DYNC2H1   93    M1991L   
2983   NaN    SLC19A2   94      P51L   
2984   NaN       LRP6   96     R611C   
2985   NaN     SLC7A9   97     G259R   
2986   NaN       TSHR   98     M453T   
2987   NaN    SLC17A5  100     H183R   
2988   NaN      ABCC6  101    R1114P   
2989   NaN       TP53  103     R273S   
2990   NaN      ACVR1  104     R258M   
2991   NaN   SLC25A15  105      G27R   
2992   NaN     PIK3CA  106    G1049S   
2993   NaN   SLC25A15  107      L71Q   
2994   NaN       LRP5  108     R752G   
2995   NaN  TNFRSF11A  109      G53R   
2996   NaN      ABCC6  111    R1459C   
2997   NaN       ASS1  113     R108L   
2998   NaN       TSHR  116     P639S   
2999   NaN       TSHR  117     F631L   
3000   NaN     RAB27A  119     A152P   
3001   NaN      PRKRA  120     P222L   
3002   NaN       OTOF  124    P1825A   
3003   NaN       BBS5  125     T183A   
3004   NaN       CRB1  126     V162M   
3005   NaN      ABCC6  128    R1138W   
3006   NaN       IDH2  129     R140W   
3007   NaN     IKBKAP  130     R696P   
3008   NaN      SMAD4  132     G386S   
3009   NaN      SCN9A  133     L858H   
3010   NaN     CREBBP  134    R1446G   
3011   NaN     NDUFS3  135     R199W   
3012   NaN       MYOT  136      S60C   
3013   NaN     NDUFS6  137     C115Y   
3014   NaN      CSF1R  138     Y571D   
3015   NaN      SCN9A  140    V1299F   
3016   NaN      DNAI1  142     G515S   
3017   NaN        GNE  143     G607E   
3018   NaN      STK11  144      R86G   
3019   NaN     PLA2G6  145      A80T   
3020   NaN      SCN4A  148    V1293I   
3021   NaN       EDAR  149     R375H   
3022   NaN      SEPT9  150      R88W   
3023   NaN       WNT4  151     A114V   
3024 

In [554]:
new_train_1.shape

(2925, 20)

In [555]:
new_test_1.shape

(619, 20)

In [148]:
new_train_1.to_csv("checkpoints_databases/new_working_train.csv",index=False,encoding="utf8")
new_test_1.to_csv("checkpoints_databases/new_working_test.csv",index=False,encoding="utf8")